# Homework 1 (Total Points: 260) <a class="anchor" id="top"></a>


**Submission instructions**:
- Only the code `TODO: Implement this!` denotes that these sections are graded.
- For Part 1: You can use the `nltk`, `numpy` and `matplotlib` libraries here. Other libraries, e.g., `gensim` or `scikit-learn`, may not be used. For Part 2: `gensim` is allowed in addition to the imported libraries in the next code cell
- The notebook you submit has to have the student ids, separated by underscores (E.g., `12341234_12341234_12341234.ipynb`). 
- This will be parsed by a regexp, so please double check your filename.
- Only one member of each group has to submit the file to canvas.
- Make sure to check that your notebook runs before submission. A quick way to do this is to restart the kernel and run all the cells.  
- Please do not delete/add new cells. Removing cells can lead to grade deduction.
- Note, that you are not allowed to use Google Colab.


**Learning Goals**:
- [Part 1, Term-based matching](#part1) (175 points):
    - Learn how to load a dataset and process it.
    - Learn how to implement several standard IR methods (TF-IDF, BM25, QL) and understand their weaknesses & strengths.
    - Learn how to evaluate IR methods.
- [Part 2, Semantic-based matching](#part2) (85 points):
    - Learn how to implement vector-space retrieval methods (LSI, LDA).
    - Learn how to use LSI and LDA for re-ranking

    
**Resources**: 
- **Part 1**: Sections 2.3, 4.1, 4.2, 4.3, 5.3, 5.6, 5.7, 6.2, 7, 8 of [Search Engines: Information Retrieval in Practice](https://ciir.cs.umass.edu/downloads/SEIRiP.pdf)
- **Part 2**: [LSI - Chapter 18](https://nlp.stanford.edu/IR-book/pdf/18lsi.pdf) from [Introduction to Information Retrieval](https://nlp.stanford.edu/IR-book/) book and the [original LDA paper](https://jmlr.org/papers/volume3/blei03a/blei03a.pdf)

In [1]:
# imports 
# TODO: Ensure that no additional library is imported in the notebook. 
# TODO: Only the standard library and the following libraries are allowed:
# TODO: You can also use unlisted classes from these libraries or standard libraries (such as defaultdict, Counter, ...).

import os
import zipfile
from functools import partial

import nltk
import requests
import numpy as np
from tqdm import tqdm

import matplotlib.pyplot as plt
from matplotlib.pyplot import cm

from ipywidgets import widgets
from IPython.display import display, HTML
#from IPython.html import widgets
from collections import namedtuple

%matplotlib inline


# Part 1: Term-based Matching (175 points) <a class="anchor" id="part1"></a>

[Back to top](#top)

In the first part, we will learn the basics of IR from loading and preprocessing the material, to implementing some well known search algorithms, to evaluating the ranking performance of the implemented algorithms. We will be using the CACM dataset throughout the assignment. The CACM dataset is a collection of titles and abstracts from the journal CACM (Communication of the ACM).

Table of contents:
- [Section 1: Text Processing](#text_processing) (15 points)
- [Section 2: Indexing](#indexing) (10 points)
- [Section 3: Ranking](#ranking) (80 points)
- [Section 4: Evaluation](#evaluation) (40 points)
- [Section 5: Analysis](#analysis) (30 points)


---
## Section 1: Text Processing (15 points)<a class="anchor" id="text_processing"></a>

[Back to Part 1](#part1)

In this section, we will load the dataset and learn how to clean up the data to make it usable for an IR system. 
The points of this section are earned for the following implementations:
- `read_cacm_docs` (4 points): Reads in the CACM documents.
- `read_queries` (3 points): Reads in the CACM queries.
- `load_stopwords` (1 point): Loads the stopwords.
- `tokenize` (4 points): Tokenizes the input text.
- `stem_token` (3 points): Stems the given token. 

We are using the [CACM dataset](http://ir.dcs.gla.ac.uk/resources/test_collections/cacm/), which is a small, classic IR dataset, composed of a collection of titles and abstracts from the journal CACM. It comes with relevance judgements for queries, so we can evaluate our IR system. 


---
### 1.1 Read the CACM documents (4 points)


The following cell downloads the dataset and unzips it to a local directory.

In [2]:
def download_dataset():
    folder_path = os.environ.get("IR1_DATA_PATH")
    if not folder_path:
        folder_path = "./datasets/"
    os.makedirs(folder_path, exist_ok=True)
    
    file_location = os.path.join(folder_path, "cacm.zip")
    
    # download file if it doesn't exist
    if not os.path.exists(file_location):
        
        url = "https://surfdrive.surf.nl/files/index.php/s/M0FGJpX2p8wDwxR/download"

        with open(file_location, "wb") as handle:
            print(f"Downloading file from {url} to {file_location}")
            response = requests.get(url, stream=True)
            for data in tqdm(response.iter_content()):
                handle.write(data)
            print("Finished downloading file")
    
    if not os.path.exists(os.path.join(folder_path, "train.txt")):
        
        # unzip file
        with zipfile.ZipFile(file_location, 'r') as zip_ref:
            zip_ref.extractall(folder_path)
        
download_dataset()

---

You can see a brief description of each file in the dataset by looking at the README file:

In [3]:
##### Read the README file 
!cat ./datasets/README
#####

Files in this directory with sizes:
          0 Jun 19 21:01 README

    2187734 Jun 19 20:55 cacm.all              text of documents
        626 Jun 19 20:58 cite.info             key to citation info
                                                (the X sections in cacm.all)
       2668 Jun 19 20:55 common_words           stop words used by smart
       2194 Jun 19 20:55 make_coll*             shell script to make collection
       1557 Jun 19 20:55 make_coll_term*        ditto (both useless without
                                                smart system)
       9948 Jun 19 20:55 qrels.text             relation giving
                                                    qid did 0 0
                                                to indicate dument did is
                                                relevant to query qid
      13689 Jun 19 20:55 query.text             Original text of the query


---
We are interested in 4 files:
- `cacm.all` : Contains the text for all documents. Note that some documents do not have abstracts available. 
- `query.text` : The text of all queries
- `qrels.text` : The relevance judgements
- `common_words` : A list of common words. This may be used as a collection of stopwords

In [4]:
##### The first 45 lines of the CACM dataset forms the first record
# We are interested only in 3 fields. 
# 1. the '.I' field, which is the document id
# 2. the '.T' field (the title) and
# 3. the '.W' field (the abstract, which may be absent)
!head -45 ./datasets/cacm.all
#####

.I 1
.T
Preliminary Report-International Algebraic Language
.B
CACM December, 1958
.A
Perlis, A. J.
Samelson,K.
.N
CA581203 JB March 22, 1978  8:28 PM
.X
100	5	1
123	5	1
164	5	1
1	5	1
1	5	1
1	5	1
205	5	1
210	5	1
214	5	1
1982	5	1
398	5	1
642	5	1
669	5	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
165	6	1
196	6	1
196	6	1
1273	6	1
1883	6	1
324	6	1
43	6	1
53	6	1
91	6	1
410	6	1
3184	6	1


In [5]:
!head -200 ./datasets/cacm.all


.I 1
.T
Preliminary Report-International Algebraic Language
.B
CACM December, 1958
.A
Perlis, A. J.
Samelson,K.
.N
CA581203 JB March 22, 1978  8:28 PM
.X
100	5	1
123	5	1
164	5	1
1	5	1
1	5	1
1	5	1
205	5	1
210	5	1
214	5	1
1982	5	1
398	5	1
642	5	1
669	5	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
165	6	1
196	6	1
196	6	1
1273	6	1
1883	6	1
324	6	1
43	6	1
53	6	1
91	6	1
410	6	1
3184	6	1
.I 2
.T
Extraction of Roots by Repeated Subtractions for Digital Computers
.B
CACM December, 1958
.A
Sugai, I.
.N
CA581202 JB March 22, 1978  8:29 PM
.X
2	5	2
2	5	2
2	5	2
.I 3
.T
Techniques Department on Matrix Program Schemes
.B
CACM December, 1958
.A
Friedman, M. D.
.N
CA581201 JB March 22, 1978  8:30 PM
.X
3	5	3
3	5	3
3	5	3
.I 4
.T
Glossary of Computer Engineering and Programming Terminology
.B
CACM November, 1958
.N
CA581103 JB March 22, 1978  8:32 PM
.X
4	5	4
4	5	4
4	5	4
.I 5
.T
Two Square-Root Approximations
.B
CACM November, 1958
.A
Wadey, W. G.
.N
CA581102 JB March 22, 1978  8:33 PM
.

In [6]:
!cat ./datasets/cite.info


4 : "bibliographic coupling" - if document id Y appears in the bibliographic
    coupling subvector for document X with a weight of w, it means X
    and Y have w common references in their bibliographies; the weight
    of did X in the vector for X is the number of items in X's bibliography.
5 : "links" - documents X and Y are linked if X cites Y, Y cites X, or
    X == Y.
6 : "co-citations" - if document id Y appears in the co-citation subvector
    for document X with weight w, it means X and Y are cited together in
    w documents; the weight of did X in the vector for X is the number
    of documents that cite X.


In [7]:
%alias head powershell -command "& {Get-Content %s -Head 500}"
%head datasets/cacm.all

/usr/bin/sh: 1: powershell: not found


---

**Implementation (4 points):**
Write a function to read the `cacm.all` file. Note that each document has a variable number of lines. The `.I` field denotes a new document:

In [8]:
# TODO: Implement this! (4 points)
def read_cacm_docs(root_folder = "./datasets/"):
    """
        Reads in the CACM documents. The dataset is assumed to be in the folder "./datasets/" by default
        Returns: A list of 2-tuples: (doc_id, document), where 'document' is a single string created by 
            appending the title and abstract (separated by a "\n"). 
            In case the record doesn't have an abstract, the document is composed only by the title
    """
    list_tup = []
    ids = []
    txt = []
    with open(root_folder + "cacm.all", 'r+') as f:
        lines = f.readlines()

        for i in range(0, len(lines)):
            line = lines[i]

            if line[:2] == ".I":
                ids.append(line[3:-1])
                
            elif line[:2] == '.T':
                count = 2
                full_title = lines[i+1]
                title = lines[i+2]
                while title[:2] != '.B':
                    
                    if title[:2] == '.W':
                        count += 1
                        full_title = full_title + lines[i+count]
                        count += 1
                        title = lines[i+count]
                        
                        while title[:2] != '.B':
                            full_title = full_title[:-1] + ' ' + title
                            count += 1
                            title = lines[i+count]
                        break

                    full_title = full_title[:-1] + ' ' + title
                    count += 1
                    title = lines[i+count]

                txt.append(full_title[:-1])

    for i in range(len(ids)):
        list_tup.append((ids[i], txt[i]))
                
    return list_tup

In [9]:
##### Function check
docs = read_cacm_docs()

assert isinstance(docs, list)
assert len(docs) == 3204, "There should be exactly 3024 documents"
##### 

---
### 1.2 Read the CACM queries (3 points)

Next, let us read the queries. They are formatted similarly:

In [10]:
##### The first 15 lines of 'query.text' has 2 queries
# We are interested only in 2 fields. 
# 1. the '.I' - the query id
# 2. the '.W' - the query
!head -15 ./datasets/query.text
#####

.I 1
.W
 What articles exist which deal with TSS (Time Sharing System), an
operating system for IBM computers?
.N
 1. Richard Alexander, Comp Serv, Langmuir Lab (TSS)
 
.I 2
.W
 I am interested in articles written either by Prieve or Udo Pooch
.A
Prieve, B.
Pooch, U.
.N
 2. Richard Alexander, Comp Serv, Langmuir Lab (author = Pooch or Prieve)


In [11]:
%head datasets/query.text

/usr/bin/sh: 1: powershell: not found


---

**Implementation (3 points):**
Write a function to read the `query.text` file:

In [12]:
# TODO: Implement this! (3 points)
def read_queries(root_folder = "./datasets/"):
    """
        Reads in the CACM queries. The dataset is assumed to be in the folder "./datasets/" by default
        Returns: A list of 2-tuples: (query_id, query)
    """
    list_tup = []
    ids = []
    txt = []
    with open(root_folder + "query.text", 'r+') as f:
        lines = f.readlines()

        for i in range(0, len(lines)):
            line = lines[i]

            if line[:2] == ".I":
                ids.append(line[3:-1])
                
            elif line[:2] == '.W':
                count = 2
                full_title = lines[i+1][1:]
                title = lines[i+2]
                while title[:2] != '.N' and title[:2] != '.A':

                    full_title = full_title[:-1] + ' ' + title
                    count += 1
                    title = lines[i+count]

                txt.append(" ".join(full_title[:-1].split()))

    for i in range(len(ids)):
        list_tup.append((ids[i], txt[i]))
                
    return list_tup

In [13]:
##### Function check
queries = read_queries()

assert isinstance(queries, list)
assert len(queries) == 64 and all([q[1] is not None for q in queries]), "There should be exactly 64 queries"
##### 

---
### 1.3 Read the stop words (1 point)

We use the common words stored in `common_words`:

In [14]:
##### Read the stop words file 
!head ./datasets/common_words
##### Read the README file 

a
about
above
accordingly
across
after
afterwards
again
against
all


In [15]:
%head datasets/common_words

/usr/bin/sh: 1: powershell: not found


---
**Implementation (1 point):**
Write a function to read the `common_words` file (For better coverage, try to keep them in lowercase):

In [16]:
# TODO: Implement this! (1 point)
def load_stopwords(root_folder = "./datasets/"):
    """
        Loads the stopwords. The dataset is assumed to be in the folder "./datasets/" by default
        Output: A set of stopwords
    """
    set_stop = set()
    with open(root_folder + "common_words", 'r+') as f:
        lines = f.readlines()

        for i in range(0, len(lines)):
            line = lines[i]

            set_stop.add(line[:-1].lower())
                
    return set_stop

In [17]:
##### Function check
stopwords = load_stopwords()

assert isinstance(stopwords, set)
assert len(stopwords) == 428, "There should be exactly 428 stop words"
##### 

---
### 1.4 Tokenization (4 points)

We can now write some basic text processing functions. 
A first step is to tokenize the text. 

**Note**: Use the  `WordPunctTokenizer` available in the `nltk` library:

In [18]:
# TODO: Implement this! (4 points)
def tokenize(text):
    """
        Tokenizes the input text. Use the WordPunctTokenizer
        Input: text - a string
        Output: a list of tokens
    """
    return nltk.WordPunctTokenizer().tokenize(text)

In [19]:
##### Function check
text = "the quick brown fox jumps over the lazy dog"
tokens = tokenize(text)

assert isinstance(tokens, list)
assert len(tokens) == 9

print(tokens)
# output: ['the', 'quick', 'brown', 'fox', 'jumps', 'over', 'the', 'lazy', 'dog']
#####

['the', 'quick', 'brown', 'fox', 'jumps', 'over', 'the', 'lazy', 'dog']


---
### 1.5 Stemming (3 points)

Write a function to stem tokens. 
Again, you can use the nltk library for this:

In [20]:
# TODO: Implement this! (3 points)
def stem_token(token):
    """
        Stems the given token using the PorterStemmer from the nltk library
        Input: a single token
        Output: the stem of the token
    """
    stemmer = nltk.PorterStemmer()
    return stemmer.stem(token)

In [21]:
##### Function check

assert stem_token('owned') == 'own'
assert stem_token('itemization') == 'item'
#####

---
### 1.6 Summary

The following function puts it all together. Given a string, it tokenizes it and processes it according to the flags that you set.

In [22]:
#### Putting it all together
def process_text(text, stem=False, remove_stopwords=False, lowercase_text=False):
    
    tokens = []
    for token in tokenize(text):
        if remove_stopwords and token.lower() in stopwords:
            continue
        if stem:
            token = stem_token(token)
        if lowercase_text:
            token = token.lower()
        tokens.append(token)

    return tokens
#### 

---

Let's create two sets of preprocessed documents.
We can process the documents and queries according to these two configurations:

In [23]:
# In this configuration:
# Don't preprocess the text, except to tokenize 
config_1 = {
  "stem": False,
  "remove_stopwords" : False,
  "lowercase_text": True
} 


# In this configuration:
# Preprocess the text, stem and remove stopwords
config_2 = {
  "stem": True,
  "remove_stopwords" : True,
  "lowercase_text": True, 
} 

####
doc_repr_1 = []
doc_repr_2 = []
for (doc_id, document) in docs:
    doc_repr_1.append((doc_id, process_text(document, **config_1)))
    doc_repr_2.append((doc_id, process_text(document, **config_2)))

####

In [24]:
doc_repr_2

[('1', ['preliminari', 'report', '-', 'intern', 'algebra', 'languag']),
 ('2', ['extract', 'root', 'repeat', 'subtract', 'digit', 'comput']),
 ('3', ['techniqu', 'depart', 'matrix', 'program', 'scheme']),
 ('4', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('5', ['squar', '-', 'root', 'approxim']),
 ('6', ['comput', 'inspect', 'procedur']),
 ('7', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('8', ['equival', 'transform', 'program', 'scheme']),
 ('9', ['propos', 'uncol']),
 ('10', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('11',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '-',
   'part',
   '2']),
 ('12', ['error', 'estim', 'rung', '-', 'kutta', 'procedur']),
 ('13', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('14',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '(',
   'part',
   '1',
   ')']),
 ('15', ['recurs', 'curv', 'fit

--- 

## Section 2: Indexing (10 points)<a class="anchor" id="indexing"></a>

[Back to Part 1](#part1)



A retrieval function usually takes in a query document pair, and scores a query against a document.  Our document set is quite small - just a few thousand documents. However, consider a web-scale dataset with a few million documents. In such a scenario, it would become infeasible to score every query and document pair. In such a case, we can build an inverted index. From Wikipedia:

> ... , an inverted index (also referred to as a postings file or inverted file) is a database index storing a mapping from content, such as words or numbers, to its locations in a table, .... The purpose of an inverted index is to allow fast full-text searches, at a cost of increased processing when a document is added to the database. ...


Consider a simple inverted index, which maps from word to document. This can improve the performance of a retrieval system significantly. In this assignment, we consider a *simple* inverted index, which maps a word to a set of documents. In practice, however, more complex indices might be used.  


### 2.1 Term Frequency-index (10 points)
In this assignment, we will be using an index created in memory since our dataset is tiny. To get started, build a simple index that maps each `token` to a list of `(doc_id, count)` where `count` is the count of the `token` in `doc_id`.
For consistency, build this index using a python dictionary.
    
Now, implement a function to build an index:

In [25]:
# TODO: Implement this! (10 points)
def build_tf_index(documents):
    """
        Build an inverted index (with counts). The output is a dictionary which takes in a token
        and returns a list of (doc_id, count) where 'count' is the count of the 'token' in 'doc_id'
        Input: a list of documents - (doc_id, tokens) 
        Output: An inverted index. [token] -> [(doc_id, token_count)]
    """
    #finding all unique tokens
    tokens_set = set()
    for doc in documents:
        for word in doc[1]:
            tokens_set.add(word)
            
    #creating a dict with counters for each doc
    inv_index = {}
    for token in tokens_set:
        inv_index[token] = []
        for doc in documents:
            counter = 0
            for word in doc[1]:
                if word == token:
                    counter += 1
            inv_index[token].append((doc[0], counter))
            
    return inv_index

In [26]:
doc_repr_2

[('1', ['preliminari', 'report', '-', 'intern', 'algebra', 'languag']),
 ('2', ['extract', 'root', 'repeat', 'subtract', 'digit', 'comput']),
 ('3', ['techniqu', 'depart', 'matrix', 'program', 'scheme']),
 ('4', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('5', ['squar', '-', 'root', 'approxim']),
 ('6', ['comput', 'inspect', 'procedur']),
 ('7', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('8', ['equival', 'transform', 'program', 'scheme']),
 ('9', ['propos', 'uncol']),
 ('10', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('11',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '-',
   'part',
   '2']),
 ('12', ['error', 'estim', 'rung', '-', 'kutta', 'procedur']),
 ('13', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('14',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '(',
   'part',
   '1',
   ')']),
 ('15', ['recurs', 'curv', 'fit

---
Now we can build indexed documents and preprocess the queries based on the two configurations:

In [28]:
#### Indexed documents based on the two configs

# Create the 2 indices
tf_index_1 = build_tf_index(doc_repr_1)
tf_index_2 = build_tf_index(doc_repr_2)

# This function returns the tf_index of the corresponding config
def get_index(index_set):
    assert index_set in {1, 2}
    return {
        1: tf_index_1,
        2: tf_index_2
    }[index_set]

####
#### Preprocessed query based on the two configs

# This function preprocesses the text given the index set, according to the specified config
def preprocess_query(text, index_set):
    assert index_set in {1, 2}
    if index_set == 1:
        return process_text(text, **config_1)
    elif index_set == 2:
        return process_text(text, **config_2)

#### 

In [29]:
##### Function check

print(tf_index_1['computer'][:10])
#### 

[('1', 0), ('2', 0), ('3', 0), ('4', 1), ('5', 0), ('6', 0), ('7', 1), ('8', 0), ('9', 0), ('10', 1)]


In [30]:
##### Function check

print(tf_index_2['computer'][:10])
#### 

[('1', 0), ('2', 0), ('3', 0), ('4', 0), ('5', 0), ('6', 0), ('7', 0), ('8', 0), ('9', 0), ('10', 0)]



---
## Section 3: Ranking  (80 points) <a class="anchor" id="ranking"></a>

[Back to Part 1](#part1)

Now that we have cleaned and processed our dataset, we can start building simple IR systems. 

For now, we consider *simple* IR systems, which involve computing scores from the tokens present in the document/query. More advanced methods are covered in later assignments.

We will implement the following methods in this section:
- [Section 3.1: Bag of Words](#bow) (10 points)
- [Section 3.2: TF-IDF](#tfidf) (15 points)
- [Section 3.3: Query Likelihood Model](#qlm) (35 points)
- [Section 3.4: BM25](#bm25) (20 points)

**Scoring policy:**
Your implementations in this section are scored based on the expected performance of your ranking functions.
You will get a full mark if your implementation meets the expected performance (measured by some evaluation metric).
Otherwise, you may get partial credit.
For example, if your *Bag of words* ranking function has 60% of expected performance, you will get 4 out of 10.

--- 

### Section 3.1: Bag of Words (10 points)<a class="anchor" id="bow"></a>

Probably the simplest IR model is the Bag of Words (BOW) model.
Implement a function that scores and ranks all the documents against a query using this model.   

Note that you can use either the count of the token or 'binarize' it i.e set the value equal to 1 if the token appears.   


In [31]:
# TODO: Implement this! (10 points)
def bow_search(query, index_set):
    """
        Perform a search over all documents with the given query. 
        Note: You have to use the `get_index` function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    index = get_index(index_set)
    processed_query = preprocess_query(query, index_set)
    
    # YOUR CODE HERE
    #index is just an index I created before, dict with key as tokens and values as list with counts and ids
    #processed_query is the string of query after all preprocessing we chossed
    
    #creating a dictionary for all ids with scores for the query (initialized with 0s)
    dict_of_scores = {}
    for i_d in index[list(index)[0]]:
        dict_of_scores[i_d[0]] = float(0)
        
    #adding the scores to dict_of_scores (binary)
    for word in processed_query:
        if word in index:
            for i_d in index[word]:
                if i_d[1] != 0:
                    dict_of_scores[i_d[0]] += float(1)
    
    #translating a dictionary to list of tuples and sorting it
    list_of_scores = list(dict_of_scores.items())
    list_of_scores.sort(key=lambda tup: tup[1], reverse=True)
    
    return list_of_scores

In [32]:
#### Function check

docs_by_id = dict(docs)
def print_results(docs, len_limit=50):    
    for i, (doc_id, score) in enumerate(docs):
        doc_content = docs_by_id[doc_id].strip().replace("\n", "\\n")[:len_limit] + "..."
        print(f"Rank {i}({score:.2}): {doc_content}")

test_bow = bow_search("report", index_set=1)[:5]
print(f"BOW Results:")
print_results(test_bow)
#### 

BOW Results:
Rank 0(1.0): Preliminary Report-International Algebraic Languag...
Rank 1(1.0): ALGOL Sub-Committee Report - Extensions...
Rank 2(1.0): The Use of Computers in Engineering Classroom Inst...
Rank 3(1.0): Report on a Conference of University Computing Cen...
Rank 4(1.0): Report on the Algorithmic Language ALGOL 60 .A Nau...


In [33]:
#### Please do not change this. This cell is used for grading.

In [34]:
#### Please do not change this. This cell is used for grading.

In [35]:
#### Please do not change this. This cell is used for grading.


---

### Section 3.2: TF-IDF (15 points) <a class="anchor" id="tfidf"></a>

Before we implement the tf-idf scoring functions, let's first write a function to compute the document frequencies of all words.  

#### 3.2.1 Document frequency (5 points)
Compute the document frequencies of all tokens in the collection.  

In [36]:
# TODO: Implement this! (5 points)
def compute_df(documents):
    """
        Compute the document frequency of all terms in the vocabulary
        Input: A list of documents
        Output: A dictionary with {token: document frequency)
    """
    # YOUR CODE HERE
    
    #finding all unique tokens
    tokens_set = set()
    for doc in documents:
        for word in doc:
            tokens_set.add(word)
            
    #creating a dict with counters for each doc
    dict_df = {}
    for token in tokens_set:
        dict_df[token] = 0
        for doc in documents:
            indicator = 0
            for word in doc:
                if word == token:
                    indicator = 1
            dict_df[token] += indicator
            
    return dict_df

In [37]:
#### Compute df based on the two configs

# get the document frequencies of each document
df_1 = compute_df([d[1] for d in doc_repr_1])
df_2 = compute_df([d[1] for d in doc_repr_2])

def get_df(index_set):
    assert index_set in {1, 2}
    return {
        1: df_1,
        2: df_2
    }[index_set]
####

In [38]:
#### Function check

print(df_1['computer'])
print(df_2['computer'])
####

597
11


In [39]:
index = get_index(index_set=1)
N = len(index[list(index)[0]])
N

3204

---
#### 3.2.2 TF-IDF search (10 points)
Next, implement a function that computes a tf-idf score given a query.      

In [40]:
# TODO: Implement this! (10 points)
def tfidf_search(query, index_set):
    """
        Perform a search over all documents with the given query using tf-idf. 
        Note #1: You have to use the `get_index` (and the `get_df`) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    index = get_index(index_set)
    df = get_df(index_set)
    processed_query = preprocess_query(query, index_set)
    
    # YOUR CODE HERE
    #creating a dictionary for all ids with scores for the query (initialized with 0s)
    dict_of_scores = {}
    for i_d in index[list(index)[0]]:
        dict_of_scores[i_d[0]] = float(0)
        
    N = len(index[list(index)[0]])
    
    #adding scores for the query
    for word in processed_query:
        if word in index:
            for i_d in index[word]:
                if i_d[1] != 0:
                    dict_of_scores[i_d[0]] += i_d[1] * np.log(N/df[word])
                    
    #translating a dictionary to list of tuples and sorting it
    list_of_scores = list(dict_of_scores.items())
    list_of_scores.sort(key=lambda tup: tup[1], reverse=True)
    
    return list_of_scores

In [41]:
#### Function check
test_tfidf = tfidf_search("report", index_set=1)[:5]
print(f"TFIDF Results:")
print_results(test_tfidf)
####

TFIDF Results:
Rank 0(2.3e+01): An Information Algebra - Phase I Report-Language S...
Rank 1(2.3e+01): Rejuvenating Experimental Computer Science\nThis r...
Rank 2(1.2e+01): ALGOL 60 Confidential\nThe ALGOL 60 Report,* when ...
Rank 3(7.8): Automatic Abstracting and Indexing Survey and Reco...
Rank 4(7.8): A String Language for Symbol Manipulation Based on...


In [42]:
#### Please do not change this. This cell is used for grading.

In [43]:
#### Please do not change this. This cell is used for grading.

In [44]:
#### Please do not change this. This cell is used for grading.

--- 

### Section 3.3: Query Likelihood Model (35 points) <a class="anchor" id="qlm"></a>

In this section, you will implement a simple query likelihood model. 


#### 3.3.1 Naive QL (15 points)

First, let us implement a naive version of a QL model, assuming a multinomial unigram language model (with a uniform prior over the documents). 



In [45]:
#### Document length for normalization

def doc_lengths(documents):
    doc_lengths = {doc_id:len(doc) for (doc_id, doc) in documents}
    return doc_lengths

doc_lengths_1 = doc_lengths(doc_repr_1)
doc_lengths_2 = doc_lengths(doc_repr_2)

def get_doc_lengths(index_set):
    assert index_set in {1, 2}
    return {
        1: doc_lengths_1,
        2: doc_lengths_2
    }[index_set]
####

In [46]:
# TODO: Implement this! (15 points)
def naive_ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a naive QL model. 
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    index = get_index(index_set)
    doc_lengths = get_doc_lengths(index_set)
    processed_query = preprocess_query(query, index_set)
    # YOUR CODE HERE
    
    dict_of_scores = {}
    for i_d in index[list(index)[0]]:
        dict_of_scores[i_d[0]] = float(1) ## how to initialize??

    for word in processed_query:
        if word in index:
            print ("word",word)
            for docID_count in index[word]: # index[word] is a list: get value (list) of the key (word). i_d is each element in the list. i_d is (doc_id, counter)
                docID = docID_count[0]
                dict_of_scores[docID] = dict_of_scores[docID] * (docID_count[1]/doc_lengths[docID])

                
    
    #translating a dictionary to list of tuples and sorting it by descending order
    list_of_scores = list(dict_of_scores.items())
    list_of_scores.sort(key=lambda tup: tup[1], reverse=True)
    print ("list_of_scores",list_of_scores)
    return list_of_scores
#naive_ql_search("report", index_set=1)
   #raise NotImplementedError()

In [47]:
#### Function check
test_naiveql = naive_ql_search("report", index_set=1)[:5]
print(f"Naive QL Results:")
print_results(test_naiveql)
####

word report
list_of_scores [('599', 0.2), ('2689', 0.2), ('1', 0.16666666666666666), ('947', 0.16666666666666666), ('65', 0.14285714285714285), ('584', 0.14285714285714285), ('985', 0.125), ('147', 0.1111111111111111), ('601', 0.1111111111111111), ('984', 0.08333333333333333), ('2583', 0.08333333333333333), ('689', 0.06666666666666667), ('196', 0.058823529411764705), ('946', 0.045454545454545456), ('1086', 0.041666666666666664), ('3184', 0.03773584905660377), ('1416', 0.03125), ('1531', 0.02857142857142857), ('3160', 0.02553191489361702), ('616', 0.020134228187919462), ('721', 0.019230769230769232), ('691', 0.017543859649122806), ('329', 0.016666666666666666), ('1659', 0.015873015873015872), ('2479', 0.015503875968992248), ('1927', 0.015151515151515152), ('644', 0.015037593984962405), ('2226', 0.014492753623188406), ('2930', 0.014492753623188406), ('321', 0.013043478260869565), ('2048', 0.01282051282051282), ('146', 0.012345679012345678), ('1765', 0.012195121951219513), ('1771', 0.0109

In [48]:
#### Please do not change this. This cell is used for grading.

In [49]:
#### Please do not change this. This cell is used for grading.

In [50]:
#### Please do not change this. This cell is used for grading.

In [51]:
#### Please do not change this. This cell is used for grading.

---
#### 3.3.2 QL (20 points)
Now, let's implement a QL model that handles the issues with the naive version. In particular, you will implement a QL model with Jelinek-Mercer Smoothing. That means an interpolated score is computed per word - one term is the same as the previous naive version, and the second term comes from a unigram language model. In addition, you should accumulate the scores by summing the **log** (smoothed) probability which leads to better numerical stability.

In [52]:
# TODO: Implement this! (20 points)

# YOUR CODE HERE
#raise NotImplementedError()

def ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a QL model 
        with Jelinek-Mercer Smoothing (set smoothing=0.1). 
        
        
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        
        
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    index = get_index(index_set)
    doc_lengths = get_doc_lengths(index_set)
    processed_query = preprocess_query(query, index_set)
    
    # YOUR CODE HERE
    smoothing = 0.1
    none_smoothing =1-smoothing
    collection_len = len (index) 
    print ("collection_len", collection_len)
    dict_of_scores = {}
    for i_d in index[list(index)[0]]:
        dict_of_scores[i_d[0]] = float(1) 
    
    for word in processed_query:
        if word in index:
            l = index[word]
            freq_in_collection = sum([pair[1] for pair in l])
            print ("word",word, "freq_in_collection", freq_in_collection)
            for docID_count in index[word]: # index[word] is a list. eg. index[word]=tf_index_1['computer']= value (a list) of the key (word). i_d is each element in the list. i_d is (doc_id, counter)
                docID = docID_count[0]
                smoothed_prob = none_smoothing * (docID_count[1]/doc_lengths[docID]) + smoothing * (freq_in_collection/collection_len)
                dict_of_scores[docID] = dict_of_scores[docID] * smoothed_prob

                
#     print ("dict_of_scores",dict_of_scores)
    list_of_scores = list(dict_of_scores.items())
    list_of_scores.sort(key=lambda tup: tup[1], reverse=True)
#     print ("list_of_scores",list_of_scores)
    return list_of_scores 
    

In [53]:
#### Function check
test_ql_results = ql_search("report", index_set=1)[:5]
print_results(test_ql_results)
print()
test_ql_results_long = ql_search("report " * 10, index_set=1)[:5]
print_results(test_ql_results_long)
####

collection_len 9698
word report freq_in_collection 84
Rank 0(0.18): A Report Writer For COBOL...
Rank 1(0.18): A CRT Report Generating System...
Rank 2(0.15): Preliminary Report-International Algebraic Languag...
Rank 3(0.15): Supplement to the ALGOL 60 Report...
Rank 4(0.13): ALGOL Sub-Committee Report - Extensions...

collection_len 9698
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
word report freq_in_collection 84
Rank 0(3.7e-08): A Report Writer For COBOL...
Rank 1(3.7e-08): A CRT Report Generating System...
Rank 2(6.1e-09): Preliminary Report-International Algebraic Languag...
Rank 3(6.1e-09): Supplement to the ALGOL 60 Report...
Rank 4(1.3e-09): ALGOL Sub-Committee Report - Extensions...


In [54]:
#### Please do not change this. This cell is used for grading.

In [55]:
#### Please do not change this. This cell is used for grading.

In [56]:
#### Please do not change this. This cell is used for grading.

In [57]:
#### Please do not change this. This cell is used for grading.

--- 

### Section 3.4: BM25 (20 points) <a class="anchor" id="bm25"></a>

In this section, we will implement the BM25 scoring function. 


In [58]:
# TODO: Implement this! (20 points)
def bm25_search(query, index_set):
    """
        Perform a search over all documents with the given query using BM25. Use k_1 = 1.5 and b = 0.75
        Note #1: You have to use the `get_index` (and `get_doc_lengths`) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    
    k=1.5
    b = 0.75
    index = get_index(index_set)
    df = get_df(index_set)
    doc_lengths = get_doc_lengths(index_set)
    processed_query = preprocess_query(query, index_set)

    #list with (doc_id,score)
    bmRes = []
    avg_doc_length = sum(list(doc_lengths.values()))/len(list(doc_lengths.values()))
    
    for i,doc in enumerate(docs):
        
        bmResult = 0
        #we loop through every word in query and compute bm25 score for every score
        for word in processed_query:
            if word in index:
                tf_w = [tf for tf in index[word] if tf[0]==doc[0]][0][1]  #term frequency calculation
                idf = np.log(len(index[word]) / df[word])   #inverse document freq calculation
                bmResult += idf*((tf_w*(k+1))/(tf_w + k*(1-b+b*doc_lengths[doc[0]]/avg_doc_length)))#bm25 score formula
            
        bmRes.append((doc[0],bmResult))
    
    bmRes = sorted(bmRes,key=lambda tup: tup[1], reverse=True) #sort list by score
    
    return bmRes
    
    
    
    
    

In [59]:
docs_by_id = dict(docs)
def print_results(docs, len_limit=50):    
    for i, (doc_id, score) in enumerate(docs):
        #if doc_id in ['2434','2863','3078']:
            doc_content = docs_by_id[doc_id].strip().replace("\n", "\\n")[:len_limit] + "..."
            print(f"Rank {i} {doc_id}({score:.2}): {doc_content}")


In [60]:
test_bm25_results = bm25_search(queries[20][1], index_set=1)[:10]
print_results(test_bm25_results)
print('~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~')
print_results(bow_search(queries[20][1], index_set=1))[:10]

Rank 0 2325(1.9e+01): Numerical Mathematics and Computer Science\nNumeri...
Rank 1 1309(1.4e+01): A Computer User-Oriented System\nA computer langua...
Rank 2 1619(1.4e+01): Error-Free Methods for Statistical Computations\nN...
Rank 3 2936(1.3e+01): An Efficient Data Structure for the Simulation Eve...
Rank 4 3166(1.3e+01): Computing Standard Deviations: Accuracy\nFour algo...
Rank 5 2702(1.3e+01): On the Complexity of LR(k) Testing\nThe problem of...
Rank 6 3018(1.2e+01): Covering Edges by Cliques with Regard to Keyword C...
Rank 7 3163(1.2e+01): An Optimal Insertion Algorithm for One-Sided Heigh...
Rank 8 2950(1.2e+01): A Unifying Approach to Scheduling\nThis paper pres...
Rank 9 2226(1.2e+01): Further Evidence for the Analysis of Algorithms fo...
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Rank 0 2189(8.0): Generation of Rosary Permutations Expressed in Ham...
Rank 1 2931(8.0): Logic and Programming Languages\nLogic has been lo...
Rank 2 719(7.0): Variable Width Stacks\nCharacter addressable, va

Rank 3030 2294(0.0): A Bonus from van Wijngaarden's Device...
Rank 3031 2295(0.0): Comment on the Composition of Semantics in Algol 6...
Rank 3032 2328(0.0): Individualizing Instruction in a Generative CAI Tu...
Rank 3033 2330(0.0): Calculation of Fourier Integrals (Algorithm R418)...
Rank 3034 2331(0.0): An Integer Programming Problem (Algorithm R397)...
Rank 3035 2332(0.0): Special Series Summation with Arbitrary Precision ...
Rank 3036 2333(0.0): Random Vectors Uniform is Solid Angle (Algorithm R...
Rank 3037 2334(0.0): General Random Number Generator (Algorithm R370)...
Rank 3038 2336(0.0): Complex Error Function (Algorithm C363)...
Rank 3039 2347(0.0): Fourier Cosine Integral [D1] (Algorithm A427)...
Rank 3040 2348(0.0): Merge Sort Algorithm [M1] (Algorithm A426)...
Rank 3041 2349(0.0): Generation of Random Correlated Normal Variables [...
Rank 3042 2351(0.0): The Optimality of Winograd's Formula...
Rank 3043 2352(0.0): Minimax Nonlinear Approximation by Approximation o...
Rank 30

TypeError: 'NoneType' object is not subscriptable

In [ ]:
queries[1][1]

In [ ]:
#### Function check
test_bm25_results = bm25_search("report", index_set=1)[:5]
print_results(test_bm25_results)
####

In [ ]:
#### Function check
bm25_search("report", index_set=1)
#print_results(test_bm25_results)
####

In [61]:
#### Please do not change this. This cell is used for grading.

In [62]:
#### Please do not change this. This cell is used for grading.

In [63]:
#### Please do not change this. This cell is used for grading.

In [64]:
#### Please do not change this. This cell is used for grading.


---

### 3.5. Test Your Functions

The widget below allows you to play with the search functions you've written so far. Use this to test your search functions and ensure that they work as expected.

In [65]:
#### Highlighter function
# class for results
ResultRow = namedtuple("ResultRow", ["doc_id", "snippet", "score"])
# doc_id -> doc
docs_by_id = dict((d[0], d[1]) for d in docs)

def highlight_text(document, query, tol=17):
    import re
    tokens = tokenize(query)
    regex = "|".join(f"(\\b{t}\\b)" for t in tokens)
    regex = re.compile(regex, flags=re.IGNORECASE)
    output = ""
    i = 0
    for m in regex.finditer(document):
        start_idx = max(0, m.start() - tol)
        end_idx = min(len(document), m.end() + tol)
        output += "".join(["...",
                        document[start_idx:m.start()],
                        "<strong>",
                        document[m.start():m.end()],
                        "</strong>",
                        document[m.end():end_idx],
                        "..."])
    return output.replace("\n", " ")


def make_results(query, search_fn, index_set):
    results = []
    for doc_id, score in search_fn(query, index_set):
        highlight = highlight_text(docs_by_id[doc_id], query)
        if len(highlight.strip()) == 0:
            highlight = docs_by_id[doc_id]
        results.append(ResultRow(doc_id, highlight, score))
    return results
####

In [66]:
# TODO: Set this to the function you want to test!
# this function should take in a query (string)
# and return a sorted list of (doc_id, score) 
# with the most relevant document in the first position
search_fn = bm25_search
index_set = 1

text = widgets.Text(description="Search Bar", width=200)
display(text)

def handle_submit(sender):
    print(f"Searching for: '{sender.value}'")
    
    results = make_results(sender.value, search_fn, index_set)
    
    # display only the top 5
    results = results[:10]
    
    body = ""
    for idx, r in enumerate(results):
        body += f"<li>Document #{r.doc_id}({r.score}): {r.snippet}</li>"
    display(HTML(f"<ul>{body}</ul>"))
    

text.on_submit(handle_submit)

Text(value='', description='Search Bar')

---

## Section 4: Evaluation (40 points) <a class="anchor" id="evaluation"></a>

[Back to Part 1](#part1)

Before we jump in and implement an algorithm for retrieval, we first have to learn how to evaluate such a system. In particular, we will work with offline evaluation metrics. These metrics are computed on a dataset with known relevance judgements.

Implement the following evaluation metrics. 

1. Precision (7 points)
2. Recall (7 points)
3. Mean Average Precision (12 points)
4. Expected Reciprocal Rank (12 points)

---
### 4.1 Read relevance labels (2 points)

Let's take a look at the `qrels.text` file, which contains the ground truth relevance scores. The relevance labels for CACM are binary - either 0 or 1. 


In [67]:
!head ./datasets/qrels.text

01 1410  0 0
01 1572  0 0
01 1605  0 0
01 2020  0 0
01 2358  0 0
02 2434  0 0
02 2863  0 0
02 3078  0 0
03 1134  0 0
03 1613  0 0


In [68]:
!head datasets/qrels.text

01 1410  0 0
01 1572  0 0
01 1605  0 0
01 2020  0 0
01 2358  0 0
02 2434  0 0
02 2863  0 0
02 3078  0 0
03 1134  0 0
03 1613  0 0


---
**Implementation (2 points):**
The first column is the query_id and the second column is the document_id. You can safely ignore the 3rd and 4th columns. Write a function to read in the file:

In [69]:
# TODO: Implement this! (2 points)
def read_qrels(root_folder = "./datasets/"):
    """
        Reads the qrels.text file. 
        Output: A dictionary: query_id -> [list of relevant documents]
    """
    # YOUR CODE HERE
    dict_qrels = {}
    with open(root_folder + "qrels.text", 'r+') as f:
        lines = f.readlines()

        for i in range(0, len(lines)):
            line = lines[i]
            if line[0] == '0':
                qid = line[1:2]
            else:
                qid = line[0:2]
                
            if qid not in dict_qrels:
                    dict_qrels[qid] = [line[3:7]]
            else:
                dict_qrels[qid].append(line[3:7])
                
    return dict_qrels

In [70]:
#### Function check
qrels = read_qrels()

assert len(qrels) == 52, "There should be 52 queries with relevance judgements"
assert sum(len(j) for j in qrels.values()) == 796, "There should be a total of 796 Relevance Judgements"
####

---
**Note:** For a given query `query_id`, you can assume that documents *not* in `qrels[query_id]` are not relevant to `query_id`. 


In [71]:
print(qrels)

{'1': ['1410', '1572', '1605', '2020', '2358'], '2': ['2434', '2863', '3078'], '3': ['1134', '1613', '1807', '1947', '2290', '2923'], '4': ['1749', '1811', '2256', '2371', '2597', '2796', '2912', '3043', '3073', '3082', '3127', '3128'], '5': ['0756', '1307', '1502', '2035', '2299', '2399', '2501', '2820'], '6': ['1543', '2078', '2828'], '7': ['1198', '1338', '1877', '1960', '2150', '2228', '2256', '2280', '2320', '2342', '2376', '2482', '2578', '2597', '2618', '2685', '2700', '2777', '2865', '2866', '2895', '2912', '2941', '3043', '3082', '3128', '3141', '3148'], '8': ['2625', '2849', '3032'], '9': ['2372', '2632', '2870', '2876', '3068', '3111', '3128', '3158', '3177'], '10': ['0046', '0141', '0392', '0950', '1158', '1198', '1262', '1380', '1471', '1601', '1613', '1747', '1795', '1811', '2060', '2150', '2256', '2289', '2342', '2376', '2433', '2618', '2664', '2685', '2700', '2714', '2777', '2785', '2851', '2895', '2896', '2912', '3039', '3075', '3156'], '11': ['1043', '1188', '1306', '

---
### 4.2 Precision (7 points)
Implement the `precision@k` metric:

In [72]:
# TODO: Implement this! (7 points)
def precision_k(results, relevant_docs, k):
    """
        Compute Precision@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), 
                    with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Precision@K
    """
    counter = 0
    for doc in results[:k]:
        if doc[0] in relevant_docs:
            counter += 1
    print(counter, "",k)
    return counter/k

In [73]:
#### Function check
qid = queries[0][0]
qtext = queries[0][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
precision = precision_k(results, qrels[qid], 10)
print(f'precision@10 = {precision}')
####

query:What articles exist which deal with TSS (Time Sharing System), an operating system for IBM computers?
2  10
precision@10 = 0.2


In [74]:
qrels[qid]

['1410', '1572', '1605', '2020', '2358']

In [75]:
qid = queries[10][0]
qtext = queries[10][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
precision = precision_k(results,qrels[qid],10)
print(f'precision@10 = {precision}')

query:SETL, Very High Level Languages
6  10
precision@10 = 0.6


---
### 4.3 Recall (7 points)
Implement the `recall@k` metric:

In [76]:
# TODO: Implement this! (7 points)
def recall_k(results, relevant_docs, k):
    """
        Compute Recall@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Recall@K
    """
    # YOUR CODE HERE
    counter = 0
    for doc in results[:k]:
        if doc[0] in relevant_docs:
            counter += 1
    #print(counter," ",len(relevant_docs))
    return counter/len(relevant_docs)

In [77]:
docs[0]

('1', 'Preliminary Report-International Algebraic Language')

In [78]:
#### Function check
qid = queries[10][0]
qtext = queries[10][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
recall = recall_k(results, qrels[qid], 10)
print(f'recall@10 = {recall}')
####

query:SETL, Very High Level Languages
recall@10 = 0.3157894736842105


---
### 4.4 Mean Average Precision (12 points)
Implement the `map` metric:

In [79]:
# TODO: Implement this! (12 points)
def average_precision(results, relevant_docs):
    """
        Compute Average Precision (for a single query - the results are 
        averaged across queries to get MAP in the next few cells)
        Hint: You can use the recall_k and precision_k functions here!
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: Average Precision
    """
    # YOUR CODE HERE
    count = 0
    for i in range(1,(len(docs)+1)):
        if results[i-1][0] in relevant_docs:
             count += precision_k(results, relevant_docs, i)
    return count / len(relevant_docs)


            
        
    #raise NotImplementedError()


In [80]:
#### Function check
qid = queries[20][0]
qtext = queries[20][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
mean_ap = average_precision(results, qrels[qid])
print(f'MAP = {mean_ap}')
####

query:computational complexity, intractability, class-complete reductions, algorithms and efficiency
1  4
2  5
3  13
4  14
5  31
6  43
7  53
8  63
9  77
10  291
11  500
MAP = 0.17269233631989397


In [81]:
#### Function check
qid = queries[0][0]
qtext = queries[0][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
mean_ap = average_precision(results, qrels[qid])
print(f'MAP = {mean_ap}')
####

query:What articles exist which deal with TSS (Time Sharing System), an operating system for IBM computers?
1  4
2  7
3  12
4  68
5  83
MAP = 0.18095575579629442


---
### 4.5 Expected Reciprocal Rank (12 points)
Implement the `err` metric:

In [82]:
# TODO: Implement this! (12 points)
def err(results, relevant_docs):
    """
        Compute the expected reciprocal rank.
        Hint: https://dl.acm.org/doi/pdf/10.1145/1645953.1646033?download=true
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: ERR
        
    """
    
    count = 0
    for i in results:
        count += 1
        if i[0] in relevant_docs:
            print(i,count)
            break
    return 1 / count
    
    

In [83]:
results[0]
#relevant_docs[0]

('2371', 19.703691823585483)

In [84]:
#### Function check
qid = queries[30][0]
qtext = queries[30][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
ERR = err(results, qrels[qid])
print(f'ERR = {ERR}')
####

query:I'd like to find articles describing the use of singular value decomposition in digital image processing. Applications include finding approximations to the original image and restoring images that are subject to noise. An article on the subject is H.C. Andrews and C.L. Patterson "Outer product expansions and their uses in digital image processing", American Mathematical Monthly, vol. 82.
('2125', 56.78547300150592) 1
ERR = 1.0


In [85]:
qid = queries[1][0]
qtext = queries[1][1]
print(f'query:{qtext}')
results = bm25_search(qtext, 2)
ERR = err(results, qrels[qid])
print(f'ERR = {ERR}')

query:I am interested in articles written either by Prieve or Udo Pooch
('2434', 0.0) 2470
ERR = 0.0004048582995951417


---
### 4.6 Evaluate Search Functions

Let's define some metrics@k using [partial functions](https://docs.python.org/3/library/functools.html#functools.partial)

In [86]:
#### metrics@k functions

recall_at_1 = partial(recall_k, k=1)
recall_at_5 = partial(recall_k, k=5)
recall_at_10 = partial(recall_k, k=10)
precision_at_1 = partial(precision_k, k=1)
precision_at_5 = partial(precision_k, k=5)
precision_at_10 = partial(precision_k, k=10)


list_of_metrics = [
    ("ERR", err),
    ("MAP", average_precision),
    ("Recall@1",recall_at_1),
    ("Recall@5", recall_at_5),
    ("Recall@10", recall_at_10),
    ("Precision@1", precision_at_1),
    ("Precision@5", precision_at_5),
    ("Precision@10", precision_at_10)]
####

---

The following function evaluates a `search_fn` using the `metric_fn`. Note that the final number is averaged over all the queries

In [87]:
#### Evaluate a search function

list_of_search_fns = [
    ("BOW", bow_search),
    ("TF-IDF", tfidf_search),
    ("NaiveQL", naive_ql_search),
    ("QL", ql_search),
    ("BM25", bm25_search)
]

def evaluate_search_fn(search_fn, metric_fns, index_set=None):
    # build a dict query_id -> query 
    queries_by_id = dict((q[0], q[1]) for q in queries)
    
    metrics = {}
    for metric, metric_fn in metric_fns:
        metrics[metric] = np.zeros(len(qrels), dtype=np.float32)
    
    for i, (query_id, relevant_docs) in enumerate(qrels.items()):
        query = queries_by_id[query_id]
        if index_set:
            results = search_fn(query, index_set)
        else:
            results = search_fn(query)
        
        for metric, metric_fn in metric_fns:
            metrics[metric][i] = metric_fn(results, relevant_docs)

    
    
    final_dict = {}
    for metric, metric_vals in metrics.items():
        final_dict[metric] = metric_vals.mean()
    
    return final_dict
####

## Section 5: Analysis (30 points) <a class="anchor" id="analysis"></a>

[Back to Part 1](#part1)

In the final section of Part1, we will compare the different term-based IR algorithms and different preprocessing configurations and analyze their advantages and disadvantages.

### Section 5.1: Plot (20 points)

First, gather the results. The results should consider the index set, the different search functions and different metrics. Plot the results in bar charts, per metric, with clear labels.

**Rubric:**
- Each Metric is plotted: 7 points
- Each Method is plotted: 7 points
- Clear titles, x label, y labels and legends (if applicable): 6 points

In [88]:
# YOUR CODE HERE
raise NotImplementedError()

NotImplementedError: 

---
### Section 5.2: Summary (10 points)
Write a summary of what you observe in the results.
Your summary should compare results across the 2 indices and the methods being used. State what you expected to see in the results, followed by either supporting evidence *or* justify why the results did not support your expectations.      

BOW

Is the simplest information retrieval  model that we use. In its essence is a simple representation of text in numbers. We represent a given document or a query as a string of numbers and the values of this string are given by the frequency of their appearance in them.  Due to its nature it comes with a number of disadvantages. It completely ignores the context of the text as we only take into account the frequency of the words that appear in there. 
This method gives a high score to words in the queries that appear multiple (with high frequency) and ignores every other factor to make a decision about the documents retrieval.

TF-IDF

In the TF_IDF model except from the term frequency we get to compute the Inverse Document frequency for every word in our corpus. It is given by dividing the total number of documents with the number of documents that this specific term appears into. We also take the logarithm of this term in order to normalize its value. IDF indicates the importance of a specific word  in our vocabulary.  TF-IDF model gives higher values to less frequent words in comparison to BOW model, but also assigns a large score to terms that their term-frequency and idf values are big, that means that this word appears in very few documents but with high frequency in them. 

QL

Query likelihood is a probabilistic model that ranks the documents by the probability that it assigns them to be retrieved, given a specific query. On a high level, it computes a probability of appearance for each term in each document and it multiplies it for all terms in the q query in order to get a rank for the d document. There is a naive approach, in which we assume a multinomial unigram language model that assigns a probability over the documents that comes from a uniform prior distribution and a more concrete approach that uses the Jelinek-Mercer Smoothing. 


BM 25 

BM25 Is a ranking function that uses as an input the queries term frequency in the document, the length of the document, the average document length, two hyperparameters that we adjust according to our preference k and b and the inverse document frequency of the query. There are many variations of this function. Generally speaking it should produce the best results in comparison to the above models for document retrieval, though our dataset is quite small so no safe conclusions are allowed. 


Plotting Conclusions

At a first glance we can immediately conclude that for set 2, in which all the words of the documents and the queries are lowercase, stemmed and we the stopwords are removed, all the implemented metrics give us a higher value in comparison with set 1. As it is also mentioned in the bibliography and the references of Information Retrieval, concerning this matter, stemming mainly improves the performance of the models as it keeps in our vocabulary the part of the word that really matters to cluster the documents into groups that they refer to a similar to the query subject. In addition removing the stop words or the very high frequency words, lead to less biased results as these words may have high frequency but they do not play a crucial role in the selection of the retrieved document.


As far as metrics are concerned ERR provides the best result with QL model approximately achieving 0,8 score out of 1. This percentage can be interpreted as 80% of the times a query is given we get a relevant document as a reply from the QL retrieval model. BOW and TF-IDF models also do achieve quite good results around 0,5.

Precision_k, is given by the division of the relevant documents that are correctly retrieved and the total number of retrieved items.  As we increase the value of  k the score of precision seems to degrade across all models. On the contrary in the Recall metric the opposite phenomenon is observed, as recall is a nondecreasing function of the number of the docs that are retrieved so if a system retrieves all docs, it would get a 100%. The observed tradeoff between precision and recall when we increase the number of the retrieved documents perfectly comes in line with the theory as in precision we penalize every document that it retrieved but is not relevant.  

QL model achieves 60% precision on average in set 2 when a single document is retrieved and BOW model around 40%. For k=5 QL precision is 40 and for k=3 around 30% respectively. 

Mean average precision combines recall and precision for ranked document retrieval. It gives the average precision scores for each relevant document that is being retrieved. In set 2 QL achieves above 30% and TF-IDF around 20%.

To sum it up, when we compare the score from the different visualised metrics we can tell that on set 2 all models seem to perform around 15-20% better on average. 


---
---
# Part 2: Semantic-based Matching (85 points) <a class="anchor" id="part2"></a>

[Back to top](#top)

We will now experiment with methods that go beyond lexical methods like TF-IDF, which operate at the word level and are high dimensional and sparse, and look at methods which constructs low dimensional dense representations of queries and documents. 

Since these low-dimensional methods have a higher time complexity, they are typically used in conjunction with methods like BM-25. That is, instead of searching through potentially million documents to find matches using low dimensional vectors, a list of K documents are retrieved using BM25, and then **re-ranked** using the other method. This is the method that is going to be applied in the following exercises. 

LSI/LDA takes documents that are similar on a semantic level - for instance, if they are describing the same topic - and projects them into nearby vectors, despite having low lexical overlap.

In this assignment, you will use `gensim` to create LSI/LDA models and use them in re-ranking. 

**Note**: The following exercises only uses `doc_repr_2` and `config_2`

Table of contents:
- [Section 6: LSI](#lsi) (15 points)
- [Section 7: LDA](#lda) (10 points)
- [Section 8: Word2Vec/Doc2Vec](#2vec) (20 points)
- [Section 8: Re-ranking](#reranking) (10 points)
- [Section 9: Re-ranking Evaluation](#reranking_eval) (30 points)

---
## Section 6: Latent Semantic Indexing (LSI) (15 points) <a class="anchor" id="lsi"></a>

[Back to Part 2](#part2)

LSI is one of the methods to embed the queries and documents into vectors. It is based on a method similar to Principal Component Analysis (PCA) for obtaining a dense concept matrix out of the sparse term-document matrix.

See [wikipedia](https://en.wikipedia.org/wiki/Latent_semantic_analysis), particularly [#Mathematics_of_LSI](https://en.wikipedia.org/wiki/Latent_semantic_analysis#Mathematics_of_LSI).

In [89]:
import gensim

In [90]:
from gensim.corpora import Dictionary
from gensim.models import LdaModel, LsiModel, Word2Vec
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim import downloader as g_downloader
# gensim uses logging, so set it up 
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

---
### Section 6.1: Cosine Similarity (5 points)<a class="anchor" id="cosing_sim"></a>
Before we begin, let us first define our method of similarity for the LSI model, the cosine similarity:

$$\text{similarity} = \cos(\theta) = {\mathbf{A} \cdot \mathbf{B} \over \|\mathbf{A}\| \|\mathbf{B}\|} = \frac{ \sum\limits_{i=1}^{n}{A_i  B_i} }{ \sqrt{\sum\limits_{i=1}^{n}{A_i^2}}  \sqrt{\sum\limits_{i=1}^{n}{B_i^2}} }$$

Since we are using gensim, the types of vectors returned by their classes are of the form defined below (they are not just simple vectors):

In [91]:
# 1, 2, 3 are either latent dimensions (LSI), or topics (LDA)
# The second value in each tuple is a number (LSI) or a probability (LDA)  
example_vec_1 = [(1, 0.2), (2, 0.3), (3, 0.4)]
example_vec_2 = [(1, 0.2), (2, 0.7), (3, 0.4)]

---
**Implementation (2+3 points):**
Now, implement the `dot product` operation on these types of vectors and using this operator, implement the `cosine similarity` (don't forget: two functions to implement!):

In [92]:
# TODO: Implement this! (2 points)
# TODO: Implement this! (2 points)
import math
def dot(vec_1,vec_2): 
    """
        vec_1 and vec_2 are of the form: [(int, float), (int, float), ...]
        Return the dot product of two such vectors, computed only on the floats
        You can assume that the lengths of the vectors are the same, and the dimensions are aligned 
            i.e you won't get: vec_1 = [(1, 0.2)] ; vec_2 = [(2, 0.3)] 
                                (dimensions are unaligned and lengths are different)
    """
    # YOUR CODE HERE
    result=0
    for num1, num2 in zip(vec_1, vec_2):
        result = result+num1[1]* num2[1]
    return result



# TODO: Implement this! (3 points)
def cosine_sim(vec_1, vec_2): 
    if vec_1 ==[] or vec_2 ==[]:
        cosine = 0
    else: 
        denominator = math.sqrt(dot(vec_1, vec_1)) * math.sqrt(dot(vec_2,vec_2)) 
        if denominator==0: 
            cosine = 0
        else:
            cosine = dot(vec_1,vec_2)/denominator
    return cosine

In [93]:
##### Function check
print(f'vectors: {(example_vec_1,example_vec_2)}')
print(f'dot product = {dot(example_vec_1,example_vec_2)}')
print(f'cosine similarity = {cosine_sim(example_vec_1,example_vec_2)}')
##### 

vectors: ([(1, 0.2), (2, 0.3), (3, 0.4)], [(1, 0.2), (2, 0.7), (3, 0.4)])
dot product = 0.41000000000000003
cosine similarity = 0.9165587597202866


In [94]:
#### Please do not change this. This cell is used for grading.

---
### Section 6.2: LSI Retrieval (10 points)<a class="anchor" id="lsi_retrieval"></a>
LSI retrieval is simply ranking the documents based on their cosine similarity to the query vector.
First, let's write a parent class for vector-based retrieval models:

In [95]:
class VectorSpaceRetrievalModel:
    """
        Parent class for Dense Vector Retrieval models
    """
    def __init__(self, doc_repr):
        """
            document_collection: 
                [
                    (doc_id_1, [token 1, token 2, ...]), 
                    (doc_id_2, [token 1, token 2, ....]) 
                    ...
                ]

        """
        self.doc_repr = doc_repr
        self.documents = [_[1] for _ in self.doc_repr]
        
        # construct a dictionary
        self.dictionary = Dictionary(self.documents)
        # Filter out words that occur less than 20 documents, or more than 50% of the documents.
        self.dictionary.filter_extremes(no_below=10)
        self.corpus = [self.dictionary.doc2bow(doc) for doc in self.documents]
    
        # Make a index to word dictionary.
        temp = self.dictionary[0]  # This is only to "load" the dictionary.
        self.id2word = self.dictionary.id2token
        
        # this is set by the train_model function
        self.model = None
        
        
    def vectorize_documents(self):
        """
            Returns a doc_id -> vector dictionary
        """
        vectors = {}
        for (doc_id, _), cc in zip(self.doc_repr, self.corpus):
            vectors[doc_id] = self.model[cc]
        return vectors

    def vectorize_query(self, query):
        # Note the use of config_2 here!
        query = process_text(query, **config_2)
        query_vector = self.dictionary.doc2bow(query)
        return self.model[query_vector]
    
    def train_model(self):
        """
            Trains a model and sets the 'self.model' variable. 
            Make sure to use the variables created in the __init__ method.
            e.g the variables which may be useful: {corpus, dictionary, id2word}
        """
        raise NotImplementedError()

In [96]:
x = VectorSpaceRetrievalModel(doc_repr_2)
#print(x.doc_repr)
v = x.vectorize_documents()
print(v)

2021-02-19 03:00:05,840 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:00:05,947 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:00:05,959 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:00:05,960 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:00:05,963 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)


TypeError: 'NoneType' object is not subscriptable

---
**Implementation (5 points):**
Implement the `train_model` method in the following class (note that this is only one line of code in `gensim`!). Ensure that the parameters defined in the `__init__` method are not changed, and are *used in the `train_method` function*. Normally, the hyperaparameter space will be searched using grid search / other methods - in this assignment we have provided the hyperparameters for you.

The last two lines of code train an LSI model on the list of documents which have been stemmed, lower-cased and have stopwords removed. 

In [97]:
# TODO: Implement this! (5 points)
class LsiRetrievalModel(VectorSpaceRetrievalModel):
    
    def __init__(self, doc_repr):
        super().__init__(doc_repr)
        
        self.num_topics = 100
        self.chunksize = 2000
    
    def train_model(self):
        # YOUR CODE HERE
        self.model = LsiModel(self.corpus, 
                              num_topics=self.num_topics,chunksize = self.chunksize)
        
       

In [98]:
#l.train_model()
doc_repr_2

[('1', ['preliminari', 'report', '-', 'intern', 'algebra', 'languag']),
 ('2', ['extract', 'root', 'repeat', 'subtract', 'digit', 'comput']),
 ('3', ['techniqu', 'depart', 'matrix', 'program', 'scheme']),
 ('4', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('5', ['squar', '-', 'root', 'approxim']),
 ('6', ['comput', 'inspect', 'procedur']),
 ('7', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('8', ['equival', 'transform', 'program', 'scheme']),
 ('9', ['propos', 'uncol']),
 ('10', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('11',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '-',
   'part',
   '2']),
 ('12', ['error', 'estim', 'rung', '-', 'kutta', 'procedur']),
 ('13', ['glossari', 'comput', 'engin', 'program', 'terminolog']),
 ('14',
  ['problem',
   'program',
   'commun',
   'chang',
   'machin',
   'propos',
   'solut',
   '(',
   'part',
   '1',
   ')']),
 ('15', ['recurs', 'curv', 'fit

In [99]:
l = LsiRetrievalModel(doc_repr_2)


2021-02-19 03:00:09,933 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:00:10,032 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:00:10,039 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:00:10,041 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:00:10,048 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)


In [100]:
##### Function check
lsi = LsiRetrievalModel(doc_repr_2)
lsi.train_model()

# you can now get an LSI vector for a given query in the following way:
lsi.vectorize_query("report")
##### 

2021-02-19 03:00:10,784 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:00:10,889 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:00:10,897 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:00:10,898 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:00:10,900 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 03:00:10,975 : WARNING : no word id mapping provided; initializing from corpus, assuming identity
2021-02-19 03:00:10,981 : INFO : using serial LSI version on this node
2021-02-19 03:00:10,982 : INFO : updating model with new documents
2021-02-19 

[(0, 0.015242649065283014),
 (1, -0.016362777662135522),
 (2, -0.0002478178586235672),
 (3, -0.0016876074803599977),
 (4, -0.009372458698592042),
 (5, -0.004689954466126108),
 (6, 0.02710338850751599),
 (7, 0.016804403310835974),
 (8, -0.03180824248397204),
 (9, -0.0006653085234868024),
 (10, 0.0020230381287451196),
 (11, -0.01711847078546651),
 (12, -0.00015525426955941002),
 (13, 0.001100192314287404),
 (14, 0.003905849687185452),
 (15, 0.0055360658440873275),
 (16, 0.005222226572998364),
 (17, 0.0022711799378529775),
 (18, -0.01940710729112329),
 (19, 0.020311201543559636),
 (20, -0.008225301688671522),
 (21, -0.013368974015453115),
 (22, 0.04835744000335267),
 (23, 0.026636222612059102),
 (24, -0.00856656107895257),
 (25, -0.010684914276471514),
 (26, 0.007216316151158975),
 (27, 0.07550435743442555),
 (28, -0.06169856547043292),
 (29, 0.031792406167540914),
 (30, 0.04489745348712179),
 (31, 0.04778077209209651),
 (32, -0.07041869715572988),
 (33, 0.051011355121280855),
 (34, -0.02

In [101]:
##### Function check
lsi = LsiRetrievalModel(doc_repr_2)
lsi.train_model()

# you can now get an LSI vector for a given query in the following way:
lsi.vectorize_documents()

2021-02-19 03:00:12,462 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:00:12,557 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:00:12,567 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:00:12,568 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:00:12,571 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 03:00:12,655 : WARNING : no word id mapping provided; initializing from corpus, assuming identity
2021-02-19 03:00:12,662 : INFO : using serial LSI version on this node
2021-02-19 03:00:12,662 : INFO : updating model with new documents
2021-02-19 

{'1': [(0, 0.47090956186814587),
  (1, 0.5280428054921785),
  (2, 0.6119865338165486),
  (3, 0.033280830673650556),
  (4, 0.48142445935080236),
  (5, 0.3730991960222271),
  (6, 0.11070617966598098),
  (7, 0.16877668618605868),
  (8, -0.6263266919241648),
  (9, 0.2634420268840881),
  (10, -0.014287108167757804),
  (11, 0.15369969163554997),
  (12, -0.2172062812994939),
  (13, -0.04104796432419285),
  (14, 0.07244725481654297),
  (15, 0.061978011775040344),
  (16, 0.016274355729881413),
  (17, 0.08118493464262194),
  (18, -0.007234601984884922),
  (19, -0.04193539416184139),
  (20, 0.15482957465409664),
  (21, -0.017140561805045074),
  (22, 0.18002907151970363),
  (23, 0.004559198052356089),
  (24, 0.007371477430182722),
  (25, 0.0001647320094384959),
  (26, 0.007787662036646352),
  (27, 0.2289438384421568),
  (28, 0.05726545803286115),
  (29, 0.06691723100080903),
  (30, 0.03426875860230115),
  (31, 0.0804131909851403),
  (32, -0.02455741894950037),
  (33, 0.044990203207366894),
  (34, 

\#### Please do not change this. This cell is used for grading.

---
Next, implement a basic ranking class for vector space retrieval (used for all semantic methods): 

In [102]:
# TODO: Implement this! (5 points)
class DenseRetrievalRanker:
    def __init__(self, vsrm, similarity_fn): 
        """
            vsrm: instance of class `VectorSpaceRetrievalModel`
            similarity_fn: function instance that takes in two vectors 
                            and returns a similarity score e.g cosine_sim defined earlier
        """
        self.vsrm = vsrm 
        self.vectorized_documents = self.vsrm.vectorize_documents()
        self.similarity_fn = similarity_fn
    

    def _compute_sim(self, query_vector):
        """
            Compute the similarity of `query_vector` to documents in 
            `self.vectorized_documents` using `self.similarity_fn`
            Returns a list of (doc_id, score) tuples
        """
        dict_of_scores = {}                   
        for key in self.vectorized_documents:  
            dict_of_scores[key] = self.similarity_fn (self.vectorized_documents[key],
                                                      query_vector) # query_vector: a list, len=100
        list_of_scores = list(dict_of_scores.items())
        return list_of_scores
    
    def search(self, query):
        scores = self._compute_sim(self.vsrm.vectorize_query(query))
        scores.sort(key=lambda _:-_[1])
        return scores 

In [103]:
##### Function check
drm_lsi = DenseRetrievalRanker(lsi, cosine_sim)
drm_lsi.search("report")[:5]
##### 

[('599', 0.7889192703202152),
 ('947', 0.5805861692233061),
 ('53', 0.4937413076877128),
 ('3160', 0.4459746536691494),
 ('1339', 0.4398862775119693)]

\#### Please do not change this. This cell is used for grading.

---
Now, you can test your LSI model in the following cell: try finding queries which are lexically different to documents, but semantically similar - does LSI work well for these queries?!

In [104]:
# test your LSI model
search_fn = drm_lsi.search

text = widgets.Text(description="Search Bar", width=200)
display(text)

def make_results_2(query, search_fn):
    results = []
    for doc_id, score in search_fn(query):
        highlight = highlight_text(docs_by_id[doc_id], query)
        if len(highlight.strip()) == 0:
            highlight = docs_by_id[doc_id]
        results.append(ResultRow(doc_id, highlight, score))
    return results

def handle_submit_2(sender):
    print(f"Searching for: '{sender.value}' (SEARCH FN: {search_fn})")
    
    results = make_results_2(sender.value, search_fn)
    
    # display only the top 5
    results = results[:5]
    
    body = ""
    for idx, r in enumerate(results):
        body += f"<li>Document #{r.doc_id}({r.score}): {r.snippet}</li>"
    display(HTML(f"<ul>{body}</ul>"))
    

text.on_submit(handle_submit_2)

Text(value='', description='Search Bar')

---
## Section 7: Latent Dirichlet Allocation (LDA) (10 points) <a class="anchor" id="lda"></a>

[Back to Part 2](#part2)

The specifics of LDA is out of the scope of this assignment, but we will use the `gensim` implementation to perform search using LDA over our small document collection. The key thing to remember is that LDA, unlike LSI, outputs a topic **distribution**, not a vector. With that in mind, let's first define a similarity measure.


---
### Section 7.1: Jenson-Shannon divergence (5 points) <a class="anchor" id="js_sim"></a>

The Jenson-Shannon divergence is a symmetric and finite measure on two probability distributions (unlike the KL, which is neither). For identical distributions, the JSD is equal to 0, and since our code uses 0 as irrelevant and higher scores as relevant, we use `(1 - JSD)` as the score or 'similarity' in our setup

**Note**: the JSD is bounded to \[0,1\] only if we use log base 2. So please ensure that you're using `np.log2` instead of `np.log`

In [105]:
## TODO: Implement this! (5 points)
def jenson_shannon_divergence(vec_1, vec_2, assert_prob=False):
    """
        Computes the Jensen-Shannon divergence between two probability distributions. 
        NOTE: DO NOT RETURN 1 - JSD here, that is handled by the next function which is already implemented! 
        The inputs are *gensim* vectors - same as the vectors for the cosine_sim function
        assert_prob is a flag that checks if the inputs are proper probability distributions 
            i.e they sum to 1 and are positive - use this to check your inputs if needed. 
                (This is optional to implement, but recommended - 
                you can the default to False to save a few ms off the runtime)
    """
    # YOUR CODE HERE
    if assert_prob == True:
        sum_1 = 0
        sum_2 = 0
        for prob in vec_1:
            if prob[1] < 0:
                print('Negative probability, wrong vector vec_1 as input.')
            sum_1 += prob[1]
            
        for prob in vec_2:
            if prob[1] < 0:
                print('Negative probability, wrong vector vec_2 as input.')
            sum_2 += prob[1]
            
        if sum_1 != 1:
            print('Probability distribiution of vec_1 does not sum up to 1!')
        if sum_2 != 1:
            print('Probability distribiutions of vec_2 does not sum up to 1!')
            
    M = []
    for i in range(len(vec_1)):
        M.append((vec_1[i][0], 1/2*(vec_1[i][1]+vec_2[i][1])))
        
    vec_1_array = np.asarray(vec_1, dtype=np.float)
    vec_2_array = np.asarray(vec_2, dtype=np.float)
    M_array = np.asarray(M, dtype=np.float)
    
    D_vec_1_M = np.sum(np.where(vec_1_array != 0, vec_1_array * np.log2(vec_1_array / M_array), 0))
    D_vec_2_M = np.sum(np.where(vec_2_array != 0, vec_2_array * np.log2(vec_2_array / M_array), 0))
    
    return 1/2*D_vec_1_M + 1/2*D_vec_2_M

def jenson_shannon_sim(vec_1, vec_2, assert_prob=False):
    return 1 - jenson_shannon_divergence(vec_1, vec_2)


In [106]:
##### Function check
vec_1 = [(1, 0.3), (2, 0.4), (3, 0.3)]
vec_2 = [(1, 0.1), (2, 0.7), (3, 0.2)]
jenson_shannon_sim(vec_1, vec_2, assert_prob=True)
##### 

0.9251064410358459

---
### Section 7.2: LDA retrieval (5 points) <a class="anchor" id="lda_ret"></a>

Implement the `train_model` method in the following class (note that this is only one line of code in `gensim`!). Ensure that the parameters defined in the `__init__` method are not changed, and are *used in the `train_method` function*. You do not need to set this. Normally, the hyperaparameter space will be searched using grid search / other methods. Note that training the LDA model might take some time

The last two lines of code train an LDA model on the list of documents which have been stemmed, lower-cased and have stopwords removed. 

In [107]:
# TODO: Implement this! (5 points)
class LdaRetrievalModel(VectorSpaceRetrievalModel):
    def __init__(self, doc_repr):
        super().__init__(doc_repr)
        
        # use these parameters in the train_model method
        self.num_topics = 100
        self.chunksize = 2000
        self.passes = 20
        self.iterations = 400
        self.eval_every = 10
        # this is need to get full vectors
        self.minimum_probability=0.0
        self.alpha='auto'
        self.eta='auto'
    
    
    def train_model(self):
        # YOUR CODE HERE
        self.model = LdaModel(corpus = self.corpus, num_topics = self.num_topics, id2word = self.id2word, 
                              chunksize = self.chunksize, passes = self.passes, iterations = self.iterations, 
                              eval_every = self.eval_every, minimum_probability = self.minimum_probability, 
                              alpha = self.alpha, eta = self.eta)

In [108]:
##### Function check
lda = LdaRetrievalModel(doc_repr_2)
lda.train_model()

# you can now get an LDA vector for a given query in the following way:
lda.vectorize_query("report")
##### 

2021-02-19 03:00:26,015 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:00:26,211 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:00:26,222 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:00:26,223 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:00:26,226 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 03:00:26,334 : INFO : using autotuned alpha, starting with [0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0

2021-02-19 03:00:30,919 : INFO : merging changes from 2000 documents into a model of 3204 documents
2021-02-19 03:00:30,955 : INFO : topic #98 (0.010): 0.130*"(" + 0.089*"algorithm" + 0.087*")" + 0.070*"search" + 0.043*"[" + 0.043*"summat" + 0.040*"modifi" + 0.040*"convers" + 0.034*"])" + 0.033*"binari"
2021-02-19 03:00:30,956 : INFO : topic #4 (0.010): 0.052*"," + 0.044*"diagnost" + 0.035*"imag" + 0.035*"reconstruct" + 0.027*"solid" + 0.026*"input" + 0.021*"comput" + 0.020*"techniqu" + 0.020*"retriev" + 0.019*"("
2021-02-19 03:00:30,956 : INFO : topic #75 (0.010): 0.194*"(" + 0.182*"algorithm" + 0.157*")" + 0.041*"[" + 0.038*"integr" + 0.028*"matrix" + 0.027*"complex" + 0.025*"])" + 0.016*"invers" + 0.013*"$"
2021-02-19 03:00:30,959 : INFO : topic #42 (0.010): 0.073*"," + 0.047*"-" + 0.024*"program" + 0.023*"system" + 0.022*"time" + 0.017*"tabl" + 0.016*"process" + 0.015*"decis" + 0.015*"comput" + 0.013*"languag"
2021-02-19 03:00:30,960 : INFO : topic #78 (0.011): 0.109*"," + 0.041*"s

2021-02-19 03:00:37,005 : INFO : topic #4 (0.009): 0.112*"imag" + 0.061*"," + 0.056*"diagnost" + 0.056*"solid" + 0.053*"reconstruct" + 0.033*"object" + 0.032*"techniqu" + 0.025*"light" + 0.018*"benefit" + 0.017*"dimension"
2021-02-19 03:00:37,005 : INFO : topic #98 (0.009): 0.155*"search" + 0.095*"modifi" + 0.093*"(" + 0.090*"algorithm" + 0.088*"convers" + 0.055*")" + 0.048*"summat" + 0.042*"binari" + 0.030*"date" + 0.030*"offer"
2021-02-19 03:00:37,006 : INFO : topic #14 (0.011): 0.087*"languag" + 0.055*"," + 0.050*"-" + 0.041*"design" + 0.039*"level" + 0.033*"system" + 0.031*"implement" + 0.025*"program" + 0.020*"type" + 0.018*"data"
2021-02-19 03:00:37,009 : INFO : topic #78 (0.012): 0.121*"," + 0.054*"system" + 0.023*"-" + 0.023*"comput" + 0.014*"manag" + 0.014*"user" + 0.013*"oper" + 0.013*"refer" + 0.012*"inform" + 0.012*"design"
2021-02-19 03:00:37,011 : INFO : topic #75 (0.012): 0.252*"(" + 0.229*")" + 0.198*"algorithm" + 0.039*"complex" + 0.029*"integr" + 0.025*"matrix" + 0.02

2021-02-19 03:00:42,179 : INFO : topic #98 (0.009): 0.209*"search" + 0.128*"convers" + 0.099*"modifi" + 0.071*"algorithm" + 0.060*"(" + 0.042*"summat" + 0.040*"binari" + 0.037*"f1" + 0.034*")" + 0.031*"number"
2021-02-19 03:00:42,181 : INFO : topic #14 (0.012): 0.121*"languag" + 0.058*"," + 0.050*"-" + 0.038*"design" + 0.035*"level" + 0.031*"implement" + 0.030*"system" + 0.027*"program" + 0.020*"data" + 0.018*"type"
2021-02-19 03:00:42,182 : INFO : topic #78 (0.012): 0.130*"," + 0.060*"system" + 0.022*"comput" + 0.022*"-" + 0.014*"oper" + 0.014*"manag" + 0.014*"user" + 0.014*"refer" + 0.013*"design" + 0.013*"inform"
2021-02-19 03:00:42,184 : INFO : topic #75 (0.015): 0.287*"(" + 0.272*")" + 0.213*"algorithm" + 0.031*"complex" + 0.026*"integr" + 0.023*"matrix" + 0.011*"invers" + 0.011*"real" + 0.009*"exponenti" + 0.008*"["
2021-02-19 03:00:42,185 : INFO : topic diff=inf, rho=0.389191
2021-02-19 03:00:43,553 : INFO : -6.565 per-word bound, 94.7 perplexity estimate based on a held-out cor

2021-02-19 03:00:48,252 : INFO : topic #55 (0.010): 0.094*"," + 0.049*"-" + 0.033*"side" + 0.032*"result" + 0.027*"comput" + 0.026*"space" + 0.024*"problem" + 0.024*"plan" + 0.019*"deriv" + 0.017*"long"
2021-02-19 03:00:48,253 : INFO : topic #14 (0.012): 0.136*"languag" + 0.062*"," + 0.042*"level" + 0.042*"design" + 0.041*"-" + 0.035*"implement" + 0.029*"program" + 0.028*"data" + 0.027*"system" + 0.018*"type"
2021-02-19 03:00:48,255 : INFO : topic #78 (0.013): 0.132*"," + 0.064*"system" + 0.021*"comput" + 0.020*"manag" + 0.020*"-" + 0.016*"refer" + 0.016*"user" + 0.015*"design" + 0.015*"oper" + 0.014*"inform"
2021-02-19 03:00:48,257 : INFO : topic #75 (0.018): 0.314*"(" + 0.300*")" + 0.211*"algorithm" + 0.030*"complex" + 0.020*"integr" + 0.019*"matrix" + 0.008*"exponenti" + 0.008*"real" + 0.007*"number" + 0.007*"invers"
2021-02-19 03:00:48,258 : INFO : topic diff=inf, rho=0.362690
2021-02-19 03:00:48,270 : INFO : PROGRESS: pass 6, at document #2000/3204
2021-02-19 03:00:49,347 : INFO :

...

2021-02-19 03:01:16,762 : INFO : topic #75 (0.049): 0.375*"(" + 0.348*")" + 0.192*"algorithm" + 0.022*"complex" + 0.015*"integr" + 0.006*"number" + 0.005*"exponenti" + 0.005*"matrix" + 0.004*"f4" + 0.004*"simpson"
2021-02-19 03:01:16,764 : INFO : topic diff=inf, rho=0.245426
2021-02-19 03:01:16,777 : INFO : PROGRESS: pass 15, at document #2000/3204
2021-02-19 03:01:17,661 : INFO : optimized alpha [0.012628041, 0.0153416535, 0.014005576, 0.013962372, 0.009785708, 0.013479499, 0.011396423, 0.0129621755, 0.012836067, 0.010889083, 0.012539875, 0.012956356, 0.011100687, 0.012067564, 0.01729488, 0.012628463, 0.013423427, 0.01447075, 0.011660198, 0.014706363, 0.011038185, 0.0118600605, 0.012425385, 0.012323009, 0.012155277, 0.013543491, 0.011256963, 0.011813426, 0.010490521, 0.010534118, 0.011366264, 0.009845588, 0.012131421, 0.010494291, 0.011428421, 0.0126043735, 0.010537966, 0.014855951, 0.011295793, 0.012092173, 0.011246872, 0.010799775, 0.013414054, 0.01326803, 0.01314593, 0.012441877, 0

2021-02-19 03:01:20,831 : INFO : topic diff=inf, rho=0.231857
2021-02-19 03:01:21,900 : INFO : -6.444 per-word bound, 87.0 perplexity estimate based on a held-out corpus of 1204 documents with 49783 words
2021-02-19 03:01:21,900 : INFO : PROGRESS: pass 16, at document #3204/3204
2021-02-19 03:01:22,765 : INFO : optimized alpha [0.012971182, 0.01588554, 0.014435732, 0.014197879, 0.009909084, 0.013894125, 0.011661929, 0.013246059, 0.013127383, 0.01105899, 0.012909633, 0.013279329, 0.011313273, 0.012440353, 0.018105123, 0.012969223, 0.0139034595, 0.015463112, 0.011851984, 0.015300859, 0.011273418, 0.0120431855, 0.012773765, 0.012806198, 0.012494693, 0.013906006, 0.011423685, 0.012145105, 0.010677266, 0.010650297, 0.011578369, 0.009939842, 0.012453343, 0.010643396, 0.011687836, 0.012890471, 0.010671259, 0.015356341, 0.0114817545, 0.0126422215, 0.011416625, 0.010986916, 0.013843578, 0.013719663, 0.013483508, 0.012751517, 0.011496964, 0.014733744, 0.011912364, 0.016175743, 0.01640518, 0.0121

2021-02-19 03:01:25,693 : INFO : topic diff=inf, rho=0.225865
2021-02-19 03:01:25,706 : INFO : PROGRESS: pass 18, at document #2000/3204
2021-02-19 03:01:26,808 : INFO : optimized alpha [0.013173591, 0.016507832, 0.014783803, 0.014801081, 0.0099893985, 0.014159282, 0.01182889, 0.013380488, 0.01347211, 0.011209476, 0.0132119665, 0.013616722, 0.011433933, 0.012646036, 0.018803127, 0.013120394, 0.01415529, 0.016312314, 0.012019593, 0.015819797, 0.011407172, 0.0121603515, 0.013023059, 0.013085373, 0.012748455, 0.01411785, 0.011531789, 0.012399576, 0.01075829, 0.010754196, 0.011718286, 0.0099925, 0.012628992, 0.010778908, 0.011838495, 0.013168308, 0.010751811, 0.015890159, 0.011571355, 0.013112279, 0.011586521, 0.01111439, 0.014044513, 0.014003244, 0.01381264, 0.013045893, 0.011630737, 0.0153663065, 0.012038896, 0.016662993, 0.01696791, 0.012420461, 0.013640902, 0.015563568, 0.013995105, 0.010131337, 0.013850898, 0.012149738, 0.011617414, 0.013983839, 0.012077232, 0.013243193, 0.01516471, 0

2021-02-19 03:01:31,671 : INFO : PROGRESS: pass 19, at document #3204/3204
2021-02-19 03:01:32,815 : INFO : optimized alpha [0.013506679, 0.017049134, 0.015213212, 0.015032111, 0.010116073, 0.014554552, 0.012096441, 0.013646282, 0.013750048, 0.011375979, 0.013584464, 0.0139389075, 0.011637909, 0.013009794, 0.019605381, 0.0134652695, 0.014622314, 0.017416203, 0.012204873, 0.016388897, 0.011646025, 0.0123375915, 0.013363663, 0.013572703, 0.013062546, 0.014451517, 0.011713873, 0.012713856, 0.010965649, 0.010865686, 0.011936483, 0.01008961, 0.012941606, 0.010928166, 0.012090632, 0.013467596, 0.010884559, 0.01636412, 0.011749914, 0.013763348, 0.011754201, 0.011292061, 0.014434071, 0.014444042, 0.014126564, 0.013381071, 0.01182727, 0.015844908, 0.012294076, 0.017343098, 0.0176785, 0.0127296625, 0.014226727, 0.01602637, 0.014655461, 0.010278985, 0.014211129, 0.012440458, 0.011844139, 0.014422544, 0.012315605, 0.01368769, 0.015521858, 0.013282214, 0.010545041, 0.013533465, 0.015356201, 0.01573

[(0, 0.005537837),
 (1, 0.006990269),
 (2, 0.006237528),
 (3, 0.006163275),
 (4, 0.0041476637),
 (5, 0.005967472),
 (6, 0.004959629),
 (7, 0.005595075),
 (8, 0.00563762),
 (9, 0.004664234),
 (10, 0.005569729),
 (11, 0.0057150535),
 (12, 0.0047716275),
 (13, 0.0053341105),
 (14, 0.008038349),
 (15, 0.005520859),
 (16, 0.0059952554),
 (17, 0.00714077),
 (18, 0.005004087),
 (19, 0.006719567),
 (20, 0.004774955),
 (21, 0.0050585023),
 (22, 0.0054791993),
 (23, 0.005564907),
 (24, 0.005355739),
 (25, 0.005925227),
 (26, 0.0048027732),
 (27, 0.0052127736),
 (28, 0.004495996),
 (29, 0.0044550104),
 (30, 0.004894045),
 (31, 0.0041368133),
 (32, 0.005306153),
 (33, 0.4144879),
 (34, 0.004957247),
 (35, 0.0055218125),
 (36, 0.0044627483),
 (37, 0.0067094085),
 (38, 0.00481755),
 (39, 0.005643073),
 (40, 0.004819308),
 (41, 0.004629827),
 (42, 0.0059180744),
 (43, 0.0059221624),
 (44, 0.0057919943),
 (45, 0.0054863365),
 (46, 0.0048492667),
 (47, 0.0064965277),
 (48, 0.005040661),
 (49, 0.0071107

\#### Please do not change this. This cell is used for grading.

---
Now we can use the `DenseRetrievalModel` class to obtain an LDA search function.
You can test your LDA model in the following cell: Try finding queries which are lexically different to documents, but semantically similar - does LDA work well for these queries?!

In [110]:
drm_lda = DenseRetrievalRanker(lda, jenson_shannon_sim)

# test your LDA model
search_fn = drm_lda.search

text = widgets.Text(description="Search Bar", width=200)
display(text)


text.on_submit(handle_submit_2)

Text(value='', description='Search Bar')

## Section 8: Word2Vec/Doc2Vec (20 points) <a class="anchor" id="2vec"></a>

[Back to Part 2](#part2)

We will implement two other methods here, the Word2Vec model and the Doc2Vec model, also using `gensim`. Word2Vec creates representations of words, not documents, so the word level vectors need to be aggregated to obtain a representation for the document. Here, we will simply take the mean of the vectors. 


A drawback of these models is that they need a lot of training data. Our dataset is tiny, so in addition to using a model trained on the data, we will also use a pre-trained model for Word2Vec (this will be automatically downloaded).     

*Note*:
1. The code in vectorize_documents / vectorize_query should return gensim-like vectors i.e `[(dim, val), .. (dim, val)]`. 
2. For Word2Vec: You should also handle the following two cases: (a) A word in the query is not present in the vocabulary of the model and (b) none of the words in the query are present in the model - you can return 0 scores for all documents in this case. For either of these, you can check if a `word` is present in the vocab by using `word in self.model`


In [112]:
# TODO: Implement this! (10 points)
import pandas as pd
class W2VRetrievalModel(VectorSpaceRetrievalModel):
    my_model = None
    def __init__(self, doc_repr):
        super().__init__(doc_repr)
        self.my_corpus = [x[1] for x in doc_repr]
        
        # the dimensionality of the vectors
        self.size = 100 
        self.min_count = 1
    
    def train_model(self):
        """
        Trains the W2V model
        """
        # YOUR CODE HERE
        self.my_model = Word2Vec(self.my_corpus,self.size,5,self.min_count)
        self.my_model.save("word2vec.model")
        #raise NotImplementedError()
        
    def vectorize_documents(self):
        """
            Returns a doc_id -> vector dictionary
        """
        # YOUR CODE HERE
        #doc_vector = model.wv
        word_list={}
                
        for d in self.doc_repr:
            gensim_list=[]
            new_list=[v for v in d[1] if v in self.my_model]
            if not new_list: continue


            result = [sum(x) for x in zip(*self.my_model[new_list])]
            results = [x/len(new_list) for x in result] 
            for i,r in enumerate(results):
                gensim_list.append((i+1,r))
        #gensim_list.append((i,(sum(w)/len(w))))
            word_list[d[0]] = gensim_list
        return word_list
        #raise NotImplementedError()
    

    def vectorize_query(self, query):
        """
        Vectorizes the query using the W2V model
        """
        query = process_text(query, **config_2)
        
        # YOUR CODE HERE
        q_new_list = [v for v in query if v in self.my_model]
              
        result = [sum(x) for x in zip(*self.my_model[q_new_list])]
        results = [x/len(q_new_list) for x in result]
#         print(self.my_model[q_new_list])
#         print("---------------")
#         print(results)
#         print("---------------")
#         print(result)
        return results
        
      
        #raise NotImplementedError()
    
    
class W2VPretrainedRetrievalModel(W2VRetrievalModel):
    def __init__(self, doc_repr):
        super().__init__(doc_repr)
        self.model_name = "word2vec-google-news-300"
        self.size = 300
    
    def train_model(self):
        """
        Loads the pretrained model
        """
        self.model = g_downloader.load(self.model_name)

w2v = W2VRetrievalModel(doc_repr_2)
w2v.train_model()

# you can now get a W2V vector for a given query in the following way:
w2v.vectorize_query("report")

2021-02-19 03:03:38,576 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 03:03:38,712 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 03:03:38,719 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 03:03:38,719 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 03:03:38,722 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 03:03:38,805 : INFO : collecting all words and their counts
2021-02-19 03:03:38,806 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2021-02-19 03:03:38,828 : INFO : collected 5940 word types from a corpus of 115982 raw w

[34.488441467285156,
 27.38172721862793,
 33.99925231933594,
 28.735980987548828,
 -31.09162139892578,
 61.758487701416016,
 21.371240615844727,
 46.02105712890625,
 -34.20293426513672,
 10.28821086883545,
 2.794992208480835,
 -6.795467376708984,
 -26.850236892700195,
 -2.281423568725586,
 8.813363075256348,
 41.54305648803711,
 -0.7472071647644043,
 34.04743576049805,
 22.219215393066406,
 63.425968170166016,
 24.971359252929688,
 -64.20457458496094,
 63.3191032409668,
 -17.415138244628906,
 -24.52228546142578,
 -19.8662109375,
 16.60750961303711,
 44.42031478881836,
 26.1605281829834,
 4.313897609710693,
 -49.7960205078125,
 -38.53700637817383,
 -21.706035614013672,
 15.913612365722656,
 54.14272689819336,
 24.623445510864258,
 -115.31233215332031,
 -47.771392822265625,
 8.41417121887207,
 58.35641860961914,
 -37.16661834716797,
 8.740575790405273,
 -10.258846282958984,
 66.95551300048828,
 7.791200160980225,
 -11.347864151000977,
 3.188953161239624,
 6.208518028259277,
 66.240776062

In [128]:
w = W2VRetrievalModel(doc_repr_2)
w.train_model()

print(w.vectorize_documents()["1"])

2021-02-19 02:41:18,256 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 02:41:18,374 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 02:41:18,386 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 02:41:18,387 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 02:41:18,392 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 02:41:18,504 : INFO : collecting all words and their counts
2021-02-19 02:41:18,505 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2021-02-19 02:41:18,524 : INFO : collected 5940 word types from a corpus of 115982 raw w

[(1, 17.982035319010418), (2, -21.26462725798289), (3, 15.122753461201986), (4, -5.060299078623454), (5, 8.453083753585815), (6, -1.7469669977823894), (7, 19.70249080657959), (8, 8.40893374880155), (9, -3.73777844508489), (10, -13.0788933634758), (11, -6.599226425091426), (12, -20.0929769774278), (13, 6.974446813265483), (14, 11.000121355056763), (15, -8.715654174486795), (16, 10.373798410097757), (17, 4.345277428627014), (18, 16.691014925638836), (19, -5.392434000968933), (20, 0.5760999520619711), (21, -8.050693988800049), (22, -17.308291127284367), (23, -10.271464109420776), (24, 18.904334942499798), (25, -1.3001124759515126), (26, -2.6205719113349915), (27, -0.6596479018529257), (28, -1.1626384258270264), (29, 18.31823968887329), (30, -10.686366538206736), (31, -6.575621326764424), (32, 3.690912206967672), (33, 8.974661111831665), (34, 1.5315383275349934), (35, -5.4730948607126875), (36, -2.1502685944239297), (37, 3.559965133666992), (38, -4.796297987302144), (39, 11.462519645690918

In [119]:
assert len(w2v.vectorize_query("report")) == 100
assert len(w2v.vectorize_query("this is a sentence that is not mellifluous")) == 100


[[ -2.6844616   -0.18089241  -8.986661    20.276411   -12.005519
   -8.6912775  -14.282996    -5.274415    10.60011      3.6817775
   -3.215986    17.274773   -10.416581    -3.150313    13.1257105
   -4.68593      2.0919113   10.460661     0.32289827   2.9872875
    1.5129863    8.006286     2.9977868    9.944548    19.942728
    8.710307     7.973123     5.52889      1.1787745    6.17709
    1.4787056  -12.125656     3.290153    -8.067093    -7.272019
   -3.80071      4.0389957   -1.7593658  -30.203888    -1.2850941
   -6.7787876   11.181952     5.46712     -5.536232     3.543678
   -6.9452176    3.6813395  -10.257477    -5.6002483   15.765114
    0.3717249   11.462119    -8.758802    -5.3166842   -0.64526135
   -0.6020273    7.9371796  -21.409872    10.3187065   -2.4247777
    7.06622      3.0438805    2.9247804  -13.668353     8.561914
   -5.3666253   -8.325002    31.270378     4.6091604    8.3860855
    7.15028    -16.519539    -1.4577354    3.6096816   -5.684081
    2.2448204  -11

/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/ipykernel_launcher.py:48: DeprecationWarning: Call to deprecated `__contains__` (Method will be removed in 4.0.0, use self.wv.__contains__() instead).
/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/ipykernel_launcher.py:50: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/ipykernel_launcher.py:51: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


\#### Please do not change this. This cell is used for grading.

In [ ]:
w2v_pretrained = W2VPretrainedRetrievalModel(doc_repr_2)
w2v_pretrained.train_model()

# you can now get an W2V vector for a given query in the following way:
w2v_pretrained.vectorize_query("report")

2021-02-19 02:41:41,473 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-02-19 02:41:41,604 : INFO : built Dictionary(5940 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...) from 3204 documents (total 115982 corpus positions)
2021-02-19 02:41:41,613 : INFO : discarding 4743 tokens: [('repeat', 8), ('glossari', 7), ('inspect', 8), ('uncol', 2), ('rung', 9), ('secant', 2), ('.', 1605), ('acceler', 6), ('diverg', 3), ('induc', 9)]...
2021-02-19 02:41:41,613 : INFO : keeping 1197 tokens which were in no less than 10 and no more than 1602 (=50.0%) documents
2021-02-19 02:41:41,617 : INFO : resulting dictionary: Dictionary(1197 unique tokens: ['-', 'algebra', 'intern', 'languag', 'preliminari']...)
2021-02-19 02:41:42,844 : INFO : loading projection weights from /home/manolis/gensim-data/word2vec-google-news-300/word2vec-google-news-300.gz
/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/smart_open/smart_open_lib.py:402: UserWarning: This

In [ ]:
##### Function check

print(len(w2v_pretrained.vectorize_query("report")))
#####

In [113]:
drm_w2v = DenseRetrievalRanker(w2v, cosine_sim)

# test your LDA model
search_fn = drm_w2v.search

text = widgets.Text(description="Search Bar", width=200)
display(text)


text.on_submit(handle_submit_2)

/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/ipykernel_launcher.py:32: DeprecationWarning: Call to deprecated `__contains__` (Method will be removed in 4.0.0, use self.wv.__contains__() instead).
/home/manolis/anaconda3/envs/py365/lib/python3.6/site-packages/ipykernel_launcher.py:36: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


Text(value='', description='Search Bar')

In [114]:
drm_w2v_pretrained = DenseRetrievalRanker(w2v_pretrained, cosine_sim)

# test your LDA model
search_fn = drm_w2v_pretrained.search

text = widgets.Text(description="Search Bar", width=200)
display(text)


text.on_submit(handle_submit_2)

NameError: name 'w2v_pretrained' is not defined

**Implementation (10 points):**
For Doc2Vec, you will need to create a list of `TaggedDocument` instead of using the `self.corpus` or `self.documents` variable. Use the document id as the 'tag'.
  

In [ ]:
# TODO: Implement this! (10 points)
class D2VRetrievalModel(VectorSpaceRetrievalModel):
    def __init__(self, doc_repr):
        super().__init__(doc_repr)
        
        self.vector_size= 100
        self.min_count = 1
        self.epochs = 20
        
        # YOUR CODE HERE
        documents = [TaggedDocument(doc, [i]), doc in enumerate(doc_repr)]
        raise NotImplementedError()
        
    def train_model(self):
        # YOUR CODE HERE
        model = Doc2Vec(documents, self.vector_size, self.min_count, self.epochs)
        raise NotImplementedError()
    
    def vectorize_documents(self):
        """
            Returns a doc_id -> vector dictionary
        """
        # YOUR CODE HERE
        vector =  model.infer_vector
        raise NotImplementedError()

    def vectorize_query(self, query):
        # YOUR CODE HERE
        raise NotImplementedError()
        
d2v = D2VRetrievalModel(doc_repr_2)
d2v.train_model()


# # you can now get an LSI vector for a given query in the following way:
d2v.vectorize_query("report")

In [ ]:
#### Please do not change this. This cell is used for grading.

\#### Please do not change this. This cell is used for grading.

In [ ]:
drm_d2v = DenseRetrievalRanker(d2v, cosine_sim)

# test your LDA model
search_fn = drm_d2v.search

text = widgets.Text(description="Search Bar", width=200)
display(text)


text.on_submit(handle_submit_2)

---
## Section 9: Re-ranking (10 points) <a class="anchor" id="reranking"></a>

[Back to Part 2](#part2)

To motivate the re-ranking perspective (i.e retrieve with lexical method + rerank with a semantic method), let's search using semantic methods and compare it to BM25's performance, along with their runtime:


In [ ]:
query = "algebraic functions"
print("BM25: ")
%timeit bm25_search(query, 2)
print("LSI: ")
%timeit drm_lsi.search(query)
print("LDA: ")
%timeit drm_lda.search(query)
print("W2V: ")
%timeit drm_w2v.search(query)
print("W2V(Pretrained): ")
%timeit drm_w2v_pretrained.search(query)
print("D2V:")
%timeit drm_d2v.search(query)

---

**Implementation (10 points):**
Re-ranking involves retrieving a small set of documents using simple but fast methods like BM25 and then re-ranking them with the aid of semantic methods such as LDA or LSI. Implement the following class, which takes in an `initial_retrieval_fn` - the initial retrieval function and `vsrm` - an instance of the `VectorSpaceRetrievalModel` class (i.e LSI/LDA) as input. The search function should first retrieve an initial list of K documents, and then these documents are re-ranked using a semantic method. This not only makes retrieval faster, but semantic methods perform poorly when used in isolation, as you will find out.

In [ ]:
# TODO: Implement this! (10 points)
class DenseRerankingModel:
    def __init__(self, initial_retrieval_fn, vsrm, similarity_fn):
        """
            initial_retrieval_fn: takes in a query and returns a list of [(doc_id, score)] (sorted)
            vsrm: instance of `VectorSpaceRetrievalModel`
            similarity_fn: function instance that takes in two vectors 
                            and returns a similarity score e.g cosine_sim defined earlier
        """
        self.ret = initial_retrieval_fn
        self.vsrm = vsrm
        self.similarity_fn = similarity_fn
        self.vectorized_documents = self.vsrm.vectorize_documents()
        
        assert len(self.vectorized_documents) == len(doc_repr_2)
    
    def search(self, query, K=50):
        """
            First, retrieve the top K results using the retrieval function
            Then, re-rank the results using the VSRM instance
        """
        # YOUR CODE HERE
        # first use initial_retrieval_fn = bm25_search_2 to get the top 50 results
        # then use vsrm = lsi to  rerank the top 50 results
        first_time_rank = self.ret(query)
        top_k = first_time_rank[:K]
        after_k = first_time_rank[k:]
        reranked = dict(top_k)
        query_vector = self.vsrm.vectorize_query(query)
        
        for docID in reranked:
            reranked [docID] = self.similarity_fn (self.vectorized_documents[docID], 
                                                   query_vector)
        list_of_scores = list(reranked.items())
        list_of_scores.sort(key=lambda _:-_[1])
        second_time_rank = list_of_scores + after_k
        return second_time_rank

In [ ]:
##### Function check
bm25_search_2 = partial(bm25_search, index_set=2)
lsi_rerank = DenseRerankingModel(bm25_search_2, lsi, cosine_sim)
lda_rerank = DenseRerankingModel(bm25_search_2, lda, jenson_shannon_sim)
w2v_rerank = DenseRerankingModel(bm25_search_2, w2v, cosine_sim)
w2v_pretrained_rerank = DenseRerankingModel(bm25_search_2, w2v_pretrained, cosine_sim)
d2v_rerank = DenseRerankingModel(bm25_search_2, d2v, cosine_sim)

##### 

\#### Please do not change this. This cell is used for grading.

---
Now, let us time the new search functions:

In [ ]:
query = "algebraic functions"
print("BM25: ")
%timeit bm25_search(query, 2)
print("LSI: ")
%timeit lsi_rerank.search(query)
print("LDA: ")
%timeit lda_rerank.search(query)
print("W2V: ")
%timeit w2v_rerank.search(query)
print("W2V(Pretrained): ")
%timeit w2v_pretrained_rerank.search(query)
print("D2V:")
%timeit d2v_rerank.search(query)

Our results from the reranking are presented below:


Running Time Before Using Reranking

query = "algebraic functions"
print("BM25: ")
%timeit bm25_search(query, 2)
print("LSI: ")
%timeit drm_lsi.search(query)
print("LDA: ")
%timeit drm_lda.search(query)

BM25: 
2.11 s ± 28.4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
LSI: 
112 ms ± 1.35 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)
LDA: 
1.24 s ± 27.9 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)

~----------------------------------------------------------------------

Running Time After Using Reranking

query = "algebraic functions"
print("BM25: ")
%timeit bm25_search(query, 2)
print("LSI: ")
%timeit lsi_rerank.search(query)
print("LDA: ")
%timeit lda_rerank.search(query)

BM25: 
2.09 s ± 43.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
LSI: 
2.1 s ± 85.5 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
LDA:
2.08 s ± 52 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)



---
As you can see, it is much faster (but BM25 is still orders of magnitude faster).

---
## Section 10: Evaluation & Analysis (30 points) <a class="anchor" id="reranking_eval"></a>

[Back to Part 2](#part2)

[Previously](#evaluation) we have implemented some evaluation metrics and used them for measuring the ranking performance of term-based IR algorithms. In this section, we will do the same for semantic methods, both with and without re-ranking.

### Section 10.1: Plot (10 points)

First, gather the results. The results should consider the index set, the different search functions and different metrics. Plot the results in bar charts, per metric, with clear labels.

Then, gather only the re-ranking models, and plot and compare them with the results obtained in part 1 (only index set 2).

In [ ]:
list_of_sem_search_fns = [
    ("lda", drm_lda.search),
    ("lsi", drm_lsi.search),
    ("w2v", drm_w2v.search),
    ("w2v_pretrained", drm_w2v_pretrained.search),
    ("d2v", drm_d2v.search),
    ("lsi_rr", lsi_rerank.search),
    ("lda_rr", lda_rerank.search),
    ("w2v_rr", w2v_rerank.search),
    ("w2v_pretrained_rr", w2v_pretrained_rerank.search),
    ("d2v_rr", d2v_rerank.search),
    
]

In [ ]:
# YOUR CODE HERE

def evaluate_search_fn_section10 (search_fn, metric_fns, index_set=None):
    # build a dict query_id -> query 
    queries_by_id = dict((q[0], q[1]) for q in queries)
    
    metrics = {}
    for metric, metric_fn in metric_fns:
        metrics[metric] = np.zeros(len(qrels), dtype=np.float32)
    
    for i, (query_id, relevant_docs) in enumerate(qrels.items()):
        query = queries_by_id[query_id]
        results = search_fn(query)
        
        for metric, metric_fn in metric_fns:
            metrics[metric][i] = metric_fn(results, relevant_docs)
            
    final_dict = {}
    for metric, metric_vals in metrics.items():
        final_dict[metric] = metric_vals.mean()
    
    return final_dict


list_of_sem_search_fns = [
    ("lda", drm_lda.search),
    ("lsi", drm_lsi.search),
    ] 

eval_all_models = []
for modelName, search_fn in list_of_sem_search_fns:
    l = [] 
    l.append (modelName)
    l.append (evaluate_search_fn_section10(search_fn, list_of_metrics, index_set=2))
    eval_all_models.append (l) # result is dict
print (eval_all_models)



modelnames = []
for i in range (0, len(eval_all_models)):
    modelnames.append (eval_all_models[i][0])
    


for i in range (0, len(list_of_metrics)):
    metric=list_of_metrics[i][0]
    set2=[]
    for i in range (0, len(eval_all_models)):
        set2.append (eval_all_models[i][1][metric])
    x = np.arange(len(eval_all_models))

    fig, ax = plt.subplots()
    width = 0.35
    ax.bar(x + width/2, set2, width, label='set2')
    ax.set_title(metric)
    ax.legend()
    ax.set_xticks(x)
    ax.set_xticklabels(modelnames)
    ax.set_ylim(0,1)
    plt.savefig('semantic methods '+str(metric)+'.png',dpi=300)
    plt.show()

### Section 10.2: Summary (20 points)

Your summary should compare methods from Part 1 and Part 2 (only for index set 2). State what you expected to see in the results, followed by either supporting evidence *or* justify why the results did not support your expectations. Consider the availability of data, scalability, domain/type of data, etc.

In the second part of the assignment we were asked to implement information retrieval models that they also incorporate the context in which the words appear inside a document. Specifically LSI, LDA, Word2Vec and Doc2Vec except from the frequency of the terms in a document, they take into account the semantic meaning or the contextual information they carry with them by being part of a document. 
Despite the above facts, we can surely tell that the metrics we have computed, using the same CACM data set, indicate that the results in the first part were by far better. 

LSI 

Latent semantic Indexing is a retrieval method that tries to identify patterns and relationships between documents and the words that they contain. This model makes the assumption that words and terms with a similar meaning are more likely to occur in the same documents or documents that discuss the same topic. The similarity between two documents is computed with the use of cosine similarity. The vocabulary is represented by a matrix with rows that they state the frequency of each word in the document and by columns that represent the different documents d. Singular value decomposition technique is used to reduce the dimensionality of the matrix, while keeping untouched the similarity and the variance of the values of the matrix. This helps alot with the need of computational resources. 



LDA

Latent Dirichlet Allocation is a model that tries to append some topics to a document that derive from the presence of some specific words that carry some attributes with them. In its gist each document is represented by a small number of topics that come from a certain word and its position in the text. 

W2V

Word to Vector is a model that takes as an input a very large corpus tokenized and produces word embeddings. More specifically, for every single word of the vocabulary it gives as an output a several hundred dimensional vector that contains numerical float values. The values and the dimension of the array of each word are assigned by taking into account the semantic distance between the words meaning and the context of the corpus that are located. 

D2V

Document to Vector model follows a similar approach as W2V, though instead of just creating a vector with values for each unique word of the corpus, it creates a vector also for each document. So by aggregating and averaging the word vectors we are able to easily conclude the similarity on a semantic and on a term based level of words, sentences and even documents. 


Plotting Conclusions

In this section we compare, the results that are depicted above by plotting the scores that the semantic models achieve in set 2, with the outputs in part 1 that come from the more simplistic models that take into account the frequency of a term in a query or a document. 
In general we can straight away tell that the models in part one, especially QL and BM 25 search, outperform by a lot  the semantic models. ERR metric once again as expected provides the best score percentage for the lsi and lda models, approximately around 20%. All the other metrics are below the above threshold for Recall, Mean Average Precision and Precision despite the value of the parameter k. 

Intuitively semantic models should have outperformed the more simplistic ones, though the nature of the data and the fact that our dataset contains a small number of text for training, probably leads to the above results. As it is also mentioned in [1] and [2] in the references section, in order to achieve high results there should be used a hybrid mixture of semantic and term frequency models, as sometimes solely semantic models fail to interpret correctly the dataset. 

References:
[1] https://www.researchgate.net/publication/274588126_A_Text_Similarity_Measurement_Combining_Word_Semantic_Information_with_TF-IDF_Method

[2]
https://www.researchgate.net/publication/330091631_Combining_semantic_and_term_frequency_similarities_for_text_clustering
